In [1]:
#_Word_Utils.py
from six import text_type as unicode
from six import string_types

#[ES] Entrada: String. Salida: String convertido al formato unicode
def word_to_unicode(w):
    if isinstance(w, string_types) and not isinstance(w, unicode):
        return unicode(w, encoding="utf-8")
    else:
        return w

#[ES]: ws: Lista de palabras. unicode: Transforma las palabras al formato unicode. lower: Transforma las palabras a minúsculas
def standarize_words(ws,unicode=False, lower=False):
    for i in range(len(ws)):
        if unicode:
            ws[i]=word_to_unicode(ws[i])
        if lower:
            ws[i] = ws[i].lower()
    return ws


In [2]:
#Vovabulary.py

from six import iteritems


class Vocabulary(object):
    word_id=[]
    id_word=[]
    
    #[ES] words: Lista de palabras. to_unicode: Transforma las palabras a formato unicode. lower: Transforma todas la palabras a minúsculas
    def __init__(self, words=[], to_unicode=True, lower = False):
        
        words = standarize_words(words,to_unicode,lower)
        
        self.word_id = {w: i for i, w in enumerate(words)}
        self.id_word = {i: w for w, i in iteritems(self.word_id)}
       
    def __len__(self):
        return len(self.word_id)
    
    @property
    def words(self):
        return list(self.word_id) 
    
    #[ES]: Dado un indice i (natural) devuelve la palabra número i del vocabulario. En caso de que no exista eleva una exepción
    def index_to_word(self,word):
        try:
            return self.id_word[word]
        except KeyError as err:
            raise
    
    #[ES]: Dada una palabra (String) devuelve la posición (natural), que ocupa en el vocabulario. En caso de que no exista eleva una exepción
    def word_to_index(self,word,default=None):
        try:
            return self.word_id[word]
        except KeyError as err:
            raise
    
    
        

In [3]:
#Embedding.py

import logging
import sys
from tqdm import tqdm
import numpy as np
from sklearn.preprocessing import normalize

class Embedding(object):
   
    vocabulary = Vocabulary()
    vectors = []
    
    #[ES] vocabulary: Objeto de la clase Vocabulary que contiene las palabras del embedding. vector: Matriz de vectores, Para i de 0 a n, la fila i se corresponderá con la palabra i del vocabulario. 
    #En caso de existir palabras duplicadas se elevará una excepción. 
    def __init__(self, vocabulary=Vocabulary(), vectors=[]):
            
        self.vocabulary = vocabulary
        self.vectors = np.array(vectors)
        
        #[EN]: Check if we have the same number of words and vectors
        #[ES]: Comprobar si tenemos el mismo numero de vectores que de palabras
        if len(self.vocabulary) != self.vectors.shape[0]:
            raise ValueError("We have a different number of words and vectors. We have {} words and {} vectors".format(len(self.vocabulary),self.vectors.shape[0]))
        
        #[EN]: Test if there are duplicated words
        #[ES]: Comprobar si tenemos palabras duplicadas
        if len(self.vocabulary) != len(set(self.vocabulary.words)):
            logging.warning("Vocabulary has duplicates")
            

    
    def __len__(self):
         return len(self.vocabulary)
    
    @property
    def words(self):
        return self.vocabulary.words
    @property
    def dims(self):
        return self.vectors.shape[1]

    #[ES] Dada una palabra (String), devuelve su vector (Array de floats). En caso de que la palabra no existe eleva una excepción
    def word_to_vector(self,word,lower=False): 
        try:
            if lower:
                return self.vectors[self.vocabulary.word_to_index(word.lower())]
            else:
                return self.vectors[self.vocabulary.word_to_index(word)]
        except KeyError as err:
            raise
            
    #[ES] Normalización L2 por filas. Para cada vector asegura que la raiz cuadrada de la suma de los cuadros es igual a 1.
    #[ES] Si replace==True se sustituarian los vectores actuales por los vectores normalizados. En caso contrario, se devolverá un nuevo embedding con las mismas palabras que el actual pero los vectores normalizados.  
    def length_normalize(self,replace=True):
        norms = np.sqrt(np.sum(self.vectors**2, axis=1))
        norms[norms == 0] = 1
        if replace:
            self.vectors = self.vectors / norms[:, np.newaxis]
            
        else:
            return Embedding(vectors = self.vectors / norms[:, np.newaxis], vocabulary=self.vocabulary)
    
    #[ES] Normalización L2 por columnas. . Para cada columna asegura que la raiz cuadrada de la suma de los cuadros es igual a 1.
    #[ES] Si replace==True se sustituarian los vectores actuales por los vectores normalizados. En caso contrario, se devolverá un nuevo embedding con las mismas palabras que el actual pero los vectores normalizados.  
    def length_normalize_dimensionwise(self,replace=True):
        norms = np.sqrt(np.sum(self.vectors**2, axis=0))
        norms[norms == 0] = 1
        if replace:
            self.vectors = self.vectors / norms
           
        else:
            return Embedding(vectors = self.vectors / norms, vocabulary=self.vocabulary)
        
    def L1_rowwise(self,replace=True):
        if replace:
            normalize(self.vectors, norm='l1', axis=1, copy=False, return_norm=False)
            
        else:
            return Embedding(vectors = normalize(self.vectors, norm='l1', axis=1, copy=True, return_norm=True), vocabulary=self.vocabulary)
    
    def L1_dimensionwwise(self,replace=True):
        if replace:
            normalize(self.vectors, norm='l1', axis=0, copy=False, return_norm=False)
            
        else:
            return Embedding(vectors = normalize(self.vectors, norm='l1', axis=0, copy=True, return_norm=True), vocabulary=self.vocabulary)
        
        
    #[ES] Para cada columna resta la media de todas las columnas del embedding
    #[ES] Si replace==True se sustituarian los vectores actuales por los vectores normalizados. En caso contrario, se devolverá un nuevo embedding con las mismas palabras que el actual pero los vectores normalizados.  
    def mean_center(self,replace=True):
        avg = np.mean(self.vectors, axis=0)
        if replace:
            self.vectors = self.vectors - avg  
           
        else:
            return Embedding(vectors = self.vectors - avg , vocabulary=self.vocabulary)
        
    #[ES] Para cada fila resta la media de todas las filas del embedding
    #[ES] Si replace==True se sustituarian los vectores actuales por los vectores normalizados. En caso contrario, se devolverá un nuevo embedding con las mismas palabras que el actual pero los vectores normalizados.
    def mean_center_embeddingwise(self,replace=True):
        avg = np.mean(self.vectors, axis=1)
        if replace:
            self.vectors = self.vectors - avg[:, np.newaxis]
           
        else:
            return Embedding(vectors = self.vectors - avg[:, np.newaxis] , vocabulary=self.vocabulary)

    #[ES] Exporta a ruta "path" el embedding actual. El formato será "dog -0.190911 -0.0466989 ... \n" si printHeader== True imprimirá al comienzo del fichero una linea que contiene el número de palabras del embedding y la longitud de los vectores del embedding
    def export(self,path,printHeader=True):
        words = self.words
        vectors = self.vectors
        
        with open(path, 'w') as file:
        
            if (printHeader):
                print('%d %d' % (len(self), self.dims), file=file)

            for i in tqdm(range(len(self))):
                print(words[i] + ' ' +' '.join(['%.6g' % x for x in vectors[i]]), file=file)

    def save(self, file):
        #@TODO cPickle
        return
        

In [1]:
#Load_embeding.py
import pandas as pd
import numpy as np
import csv
from sys import stdout
from IPython.display import clear_output
import logging
from tqdm import tqdm
import io
from six import text_type   
import codecs

#[ES] Carga un embedding desde un directorio, devuelve un objeto del tipo embedding.
#[ES] Parámetros:
    #path: Ruta (obligatorio)
    #format: text, archivo de texto, con o sin encabezado. bin archivo binario (w2v). senna modo especial para estos embeddings. vgg modo especial para los embedding de imágenes. DT_embedddings: Modo espacial para leer estos embeddings
    #vocabulary: Si es None cargará todas las palabras del fichero, si es una lista de palabras [cat, dog...] solo se cargarán las palabras pertenecientes a esa lista, útil si solo se quiere evaluar los embeddings en unos datasets
    #length_normalize: Normalización L2 por filas de los embeddings cargados
    #normalize_dimensionwise: Normalización L2 por columanas de los embeddigs cargados. 
        #En caso de que length_normalize y normalize_dimensionwise sean TRUE. Primero se realiza la normalización por columnas y después por filas.
    #to_unicode: Transforma a unicode las palabras del embedding
    #lower: Transforma a minúsculas las palabras del emnedding
    #path2: En caso de que el formato sea "senna" o "DT_embedings" en path irá el fichero con las palabras, y en path2 el fichero con los vectores
    #dims_restricton: Entero i (dimensiones del embedding). Por cada fila leida se tomará como número los elementos n..n-i y los elementos 0..n-i-1 se concaterán y serán tomados como palabra. Muy útil para embeddings con palabras que contienen espacio o carácteres extraños que son tomados como espacios.
    #delete_duplicates: Elimina los duplicados del embeddig, por cada palabra duplicada se mantendrá solo la primera que aparezca en el fichero. Solo recomendable para embeddings con mucha suciedad como los obtenidos de common crawl, donde algunas palabras con caracteres extraños no reconocidos por python se leen como si fueran la misma, eliminar estas palabras no tiene impacto alguno en el embedding, por ejemplo en el caso de FastText CC solo se eliminan 4 palabras.
    #method_vgg: En caso de que el formato sea "vgg", si este atributo es "delete" se eliminarán los duplicados de la misma forma explicada en el atributo anterior. En caso de que sea "average" se hará la media de los vectores de las palabras duplicadas. Este es un embedding que tiene la peculiaridad de tener un gran número de duplicados
    
def load_embedding(path, format="text", vocabulary = None, length_normalize=True, normalize_dimensionwise = False, to_unicode=True, lower=False, path2='',dims_restriction=None, delete_duplicates=False, method_vgg = "delete"):
    assert format in ["text","bin","senna","vgg","DT_embeddings"], "Unrecognized format"
    
    if vocabulary is not None:
        if len(set(vocabulary)) != len(vocabulary):
            logging.warning("Provided vocabulary has duplicates. IMPORTANT NOTE: The embedding that this function will return will not have duplicates.")
    
    if format == "text":
        vocab, matrix = from_TXT(path,vocabulary,dims_restriction)
    
    if format == "bin":
        vocab, matrix = from_BIN(path,vocabulary)
    
    if format == "senna":
        vocab, matrix = from_SENNA(path,path2)
    
    if format == "vgg":
        vocab, matrix = from_vgg(path,method_vgg)
    
    if format == "DT_embeddings":
        vocab, matrix = from_DT_embeddings(path,path2)
    
    if delete_duplicates:
        remove_duplicates(vocab,matrix)
    
    vocabulary = Vocabulary(vocab,to_unicode,lower)
    e = Embedding(vocabulary=vocabulary,vectors = matrix)
    
    if normalize_dimensionwise:
        e.length_normalize_dimensionwise()
    
    if length_normalize:
        e.length_normalize()
        
    return e

def has_header(path,vocabulary = None):
    with open(path) as f:
        first_line = f.readline()
        first_line = first_line.split(' ')
        if len(first_line)==2:
            return 1
        return 0

def remove_duplicates(words,vectors):
    seen = set()
    seen_add = seen.add
    duplicate_indexes = [idx for idx,item in enumerate(words) if item in seen or seen_add(item)]
    for d in reversed(duplicate_indexes):
        logging.warning("Word {} deleted".format((words[d])))
        del(words[d])
        del(vectors[d])
    
    
    

def from_TXT(path, vocabulary=None, dims_restriction = None):
    words = []
    vectors = []
    
    #with codecs.open(path, "r",encoding='utf-8', errors='ignore') as f:
    with open(path) as f:
        if has_header:
            next(f)
        for line_no, line in enumerate(f):
            l = line.split()
            
            if vocabulary is None:
                try:
                    if not dims_restriction:
                        vectors.append(np.asarray(l[1:]).astype(np.float32))
                        words.append(l[0])
                    else:
                        wi = len(l)-dims_restriction
                        st = ''.join(l[0:wi])
                        words.append(st)
                        vectors.append(np.asarray(l[wi:]).astype(np.float32))
                        
                except ValueError:
                    logging.warning("Line {}.Error reading the vector for the word {}... Word has been omitted".format(line_no,l[0:3]))
                    
                        
            elif l[0] in vocabulary:
                try:
                    if not dims_restriction:
                        vectors.append(np.asarray(l[1:]).astype(np.float32))
                        words.append(l[0])
                    else:
                        wi = len(l)-dims_restriction
                        st = ''.join(l[0:wi])
                        words.append(st)
                        vectors.append(np.asarray(l[wi:]).astype(np.float32))
                except ValueError:
                    logging.warning("Line {}.Error reading the vector for the word {}... Word has been omitted".format(line_no,l[0:3]))
                    
    return words, vectors    
            
    



def from_BIN(path,vocabulary = None):
    with io.open(path,'rb') as file:
        words = []
        
        header = file.readline()
        vocab_size, layer1_size = list(map(int, header.split()))
        vocab_size_aux = vocab_size

        if vocabulary is None:
            vectors = np.zeros((vocab_size, layer1_size), dtype=np.float32)
        else:
            vectors = []

        binary_len = np.dtype("float32").itemsize * layer1_size
        for line in tqdm(range(vocab_size)):
            word = []
            while True:
                ch = file.read(1)
                if ch == b' ':
                    break
                if ch != b'\n':
                    word.append(ch)

            if vocabulary is None:
               
                words.append(b''.join(word).decode("latin-1"))
            
                vectors[line, :] = np.fromstring(file.read(binary_len), dtype=np.float32)
                
            else:
                w = b''.join(word).decode("latin-1")
                if w in vocabulary:
                    words.append(w)
                    vectors.append(np.fromstring(file.read(binary_len), dtype=np.float32))

                else:
                    vocab_size_aux-=1
                    file.read(binary_len)
                
                    
        if len(words) != vocab_size_aux:
            raise ValueError("Header says that there are {} words, but {} were read".format(vocab_size_aux,len(words)))

        return words, vectors

    
    
def from_SENNA(path_words,path_vectors):
    words = []
    vectors = []
    
    with open(path_words) as f:
        for line in f:
            l = line.split()
            words.append(l[0])
                
    with open(path_vectors) as f:
        for line in f:
            l = line.split()
            vectors.append(np.asarray(l).astype(np.float32))
    return words, vectors

    
def from_vgg(path,method_vgg = "delete"):
    
    data = pd.read_csv(path, sep=',', header=None)
    words = []
    vectors = []
    for i in range(len(data.index)):
        w = data.iloc[i,0]
        if w not in words:
                words.append(w)
                vectors.append(np.array(data.iloc[i,1:]).astype(np.float32))
        else:
            if method_vgg == "mean":
                ind = words.index(w)
                vectors[ind] = (vectors[ind] + np.array(data.iloc[i,1:]).astype(np.float32))/2
                
                
    return words, vectors


def from_DT_embeddings(path_nodes, path_vectors):
    vectors = []
    nodes = {}
    words =[]
    with codecs.open(path_nodes, "r",encoding='utf-8', errors='ignore') as fnodes:
        for line_no, line in enumerate(fnodes):
            wt,wn = line.split()
            w = wt.split('/')[0]
            nodes.update({wn:w})
    
    with codecs.open(path_vectors, "r",encoding='utf-8', errors='ignore') as fwords:
        next(fwords)
        for line_no, line in enumerate(fwords):
            l = line.split()
            vectors.append(np.asarray(l[1:]).astype(np.float32))
            words.append(nodes[l[0]])        
            
    return words,vectors
            
            
        

In [5]:
#similarity.py
import scipy.stats
from tqdm import tqdm
import matplotlib.pyplot as plt

#[ES] Calcula la similitud coseno entre dos vectores dados. 
def calculate_cosine_simil(vector1, vector2):
    return np.dot(vector1,vector2)/(np.linalg.norm(vector1)*np.linalg.norm(vector2))
    
    #if isNormalized:
    #    return np.dot(vector1,vector2)
    #else:
    #    return np.dot(vector1,vector2)/(np.linalg.norm(vector1)*np.linalg.norm(vector2))

#[ES] Dado un embedding y dos palabras (string), devulve la similitud coseno entre ambas palabras, en caso de que alguna de las dos no exista en el embeddig se devolverá None
def similarity_2_words(e,word1,word2, lower = False): 
    try:
        v1 = e.word_to_vector(word1,lower)
    except KeyError as err:
        logging.critical("The word {} does not exits in the embeding".format(word1))
        return None
    try:
        v2 = e.word_to_vector(word2,lower)
    except KeyError as err:
        logging.critical("The word {} does not exits in the embeding".format(word2))
        return None
   

    return calculate_cosine_simil(v1, v2)

    
    
#[ES] Entrada.
        #embedding: a evaluar
        #X lista de pares de palabras
        #gold: Resultados de la similitud entre los pares de palabras
        #backoff_embs: Lista de embeddings, en caso de que alguna palabra de los pares no se encuentre en el embedding a evaluar, utilizará un embedding de la lista en lugar del que se va a evaluar para ese par de palabras (se toman ambas palabras del embedding backoff), primero se probará con el primero de lista, después con el segundo...
    # Salida:
        #coverage: Porcentaje de pares para los que se ha podido dar una respuesta del total de pares de palabras
        #pearson: Correlación de pearson entre los resultados de similaridad del embedding y los proporcionado
        #spearman: Correlación de spearman entre los resultados de similaridad del embedding y los proporcionado
def similarity_emd(embedding, X, gold, backoff_embs=None, lower = False):
    rescsv = ''
    results = []
    gold_scores = []
    oov = 0
    for gold_score in tqdm(range(len(gold))):
        try:
            cos = calculate_cosine_simil(
                                         embedding.word_to_vector(X[gold_score][0],lower), 
                                         embedding.word_to_vector(X[gold_score][1],lower))
            results.append(cos)
            rescsv = str(rescsv)  + str(cos) + ','
            gold_scores.append(gold[gold_score])
            
        except KeyError as err:
            if backoff_embs is None:
                oov+=1
                print(X[gold_score])
            else:
                actual_emb=0
                for e in backoff_embs:
                    try:
                        cos = calculate_cosine_simil(
                                         e.word_to_vector(X[gold_score][0],lower), 
                                         e.word_to_vector(X[gold_score][1],lower))
                        results.append(cos)
                        
                        gold_scores.append(gold[gold_score])
                        break
                    except KeyError as err:
                        if actual_emb == len(backoff_embs)-1:
                             oov+=1
                    
                    actual_emb+=1
        
        
    #ts = Series(results, index=list(range(0, len(results))))
    #ts = ts.cumsum()
    #ts.plot()
    #print("==========RESULTS===============")
    #print(rescsv)
    
    coverage = len(results)/(len(results) + oov)
    pearson = scipy.stats.pearsonr(gold_scores, results)[0]
    spearman = scipy.stats.spearmanr(gold_scores, results)[0]
        
    return{'coverage':coverage, 'pearson':pearson, 'spearman':spearman}

def average_similarity(embeddings, X, gold, weights = None, lower=False):
    
    if weights is not None and len(embeddings)!=len(weights):
        raise ValueError("Embedding and weights must have the same length")
    
    results = []
    gold_scores = []
    oov = 0
    for gold_score in tqdm(range(len(gold))):
        avgW=0
        avg = []
        e = 0
        div = 0
        for emb in range(len(embeddings)):
            try:
                cos = calculate_cosine_simil(
                                         embeddings[emb].word_to_vector(X[gold_score][0],lower), 
                                         embeddings[emb].word_to_vector(X[gold_score][1],lower))
                if weights is None:     
                    avg.append(cos)
                else:
                    avgW+=cos*weights[emb]
                    div+=weights[emb]
            except KeyError as err:
                e+=1
        
        if e<len(embeddings):
        #if e == 0:   
            if weights is None:
                results.append(np.mean(avg))
            else:
                results.append(avgW/div)
                
            gold_scores.append(gold[gold_score])
        else:
            oov+=1
    
    coverage = len(results)/(len(results) + oov)
    pearson = scipy.stats.pearsonr(gold_scores, results)[0]
    spearman = scipy.stats.spearmanr(gold_scores, results)[0]
        
    return{'coverage':coverage, 'pearson':pearson, 'spearman':spearman}



In [6]:
scipy.stats.mstats.gmean(abs([-0.12312]))

TypeError: bad operand type for abs(): 'list'

In [7]:
# similarity datasets
from sklearn.datasets.base import Bunch
from six import iteritems
import pandas as pd
import csv
from pandas import Series, DataFrame

dataset_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/SimilarityDataset/'

Mturk287_path = dataset_path + 'EN-MTurk-287.txt'
Mturk771_path = dataset_path + 'EN-MTurk-771.txt' 
mendev_path = dataset_path + 'EN-MEN-LEM-DEV.txt' 
mentest_path = dataset_path + 'EN-MEN-LEM-TEST.txt' 
men_path = dataset_path + 'EN-MEN-LEM.txt' 
WS353_all_path = dataset_path + 'EN-WS353_all.txt'
WS353_relaredness_path = dataset_path + 'EN-WSR353_relatedness.txt'
WS353_similarity_path = dataset_path + 'EN-WSS353_similarity.txt'
WS353_set1_path = dataset_path + 'EN-WS353-SET1.txt'
WS353_set2_path = dataset_path + 'EN-WS353-SET2.txt'
RG65_path =dataset_path + 'EN-RG-65.txt'
RW_path = dataset_path + 'EN-RW.txt'
SIM999_path = dataset_path + 'EN-SIM999.txt'
Verb143_path = dataset_path + 'EN-VERB-143.txt'
MC30_path = dataset_path + 'EN-MC-30.txt'
YP_130_path = dataset_path + 'EN-YP-130.txt'
SimVerb3500_path = dataset_path + 'EN-SimVerb-3500.txt'

def get_MTurk287():
    data = pd.read_csv(Mturk287_path, sep="\t", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y=2 * data[:,2].astype(np.float))

def get_MTurk771():
    data = pd.read_csv(Mturk771_path, sep=" ", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y=2 * data[:,2].astype(np.float))

def get_MENdev():
    data = pd.read_csv(mendev_path, sep=" ", header=None)
    data = data.apply(lambda x: [y if isinstance(y, float) else y[0:-2] for y in x])
    return Bunch(X=data.values[:,0:2].astype("object"), y= data.values[:,2].astype(np.float)/ 5.0)

def get_MENtest():
    data = pd.read_csv(mentest_path, sep=" ", header=None)
    data = data.apply(lambda x: [y if isinstance(y, float) else y[0:-2] for y in x])
    return Bunch(X=data.values[:,0:2].astype("object"), y= data.values[:,2].astype(np.float)/ 5.0)


def get_MENall():
    data = pd.read_csv(men_path, sep=" ", header=None)
    data = data.apply(lambda x: [y if isinstance(y, float) else y[0:-2] for y in x])
    return Bunch(X=data.values[:,0:2].astype("object"), y= data.values[:,2].astype(np.float)/ 5.0)

def get_WS353_all():
    data = pd.read_csv(WS353_all_path, sep="\t", header=0).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float))

def get_WS353_relatedness():
    data = pd.read_csv(WS353_relaredness_path, sep="\t", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float))

def get_WS353_similarity():
    data = pd.read_csv(WS353_similarity_path, sep="\t", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float))

def get_WS353_set1():
    data = pd.read_csv(WS353_set1_path, sep="\t", header=0).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float))

def get_WS353_set2():
    data = pd.read_csv(WS353_set2_path, sep="\t", header=0).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float))

def get_RG65():
    data = pd.read_csv(RG65_path, sep="\t", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float) * 10.0 / 4.0)

def get_RW():
    data = pd.read_csv(RW_path, sep="\t", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float))

def get_SimLex999():    
    data = pd.read_csv(SIM999_path, sep="\t", header=0).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,3].astype(np.float))

def get_Verb143():
    data = pd.read_csv(Verb143_path, sep="\t", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float)*10.0)

def get_MC30():
    data = pd.read_csv(MC30_path, sep="\t", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float) * 10.0 / 4.0)

def get_YP130():
    data = pd.read_csv(YP_130_path, sep=" ", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float) * 10.0 / 4.0)

def get_SimVerb3500():
    data = pd.read_csv(SimVerb3500_path, sep="\t", header=None).values
    return Bunch(X=data[:,0:2].astype("object"), y= data[:,2].astype(np.float))



datasets = {
        "SimLex999": get_SimLex999(),
        "MTurk-287": get_MTurk287(),
        "MTurk-771": get_MTurk771(),
        "MEN_DEV": get_MENdev(),
        "MEN_TEST": get_MENtest(),
        "MEN_ALL": get_MENall(),
        "WS353_all": get_WS353_all(),
        "WS353_relatedness": get_WS353_relatedness(),
        "WS353_similarity": get_WS353_similarity(),
        "WS353_set1": get_WS353_set1(),
        "WS353_set2": get_WS353_set2(),
        "RG65": get_RG65(),
        "VERB-143": get_Verb143(),
        "MC-30": get_MC30(),
        "YP-130": get_YP130(),
        "SimVerb-3500": get_SimVerb3500(),
        "RW": get_RW()
    
    }
    

def get_vocab_simil_all(lower=False):
    vocab = []
    for name, data in iteritems(datasets):
            vocab = np.append(vocab, np.append((data.X[:,0]),(data.X[:,1])))
    if lower:
        for i in range(len(vocab)):
            vocab[i]=vocab[i].lower()
    return set(vocab)  

def get_dataset(dataset):
    if dataset == 'MTurk-287':
        return get_MTurk287()
    elif dataset == 'MTurk-771':
        return get_MTurk771()
    elif dataset == 'MEN':
        return  get_MENall()
    elif dataset == 'WS353_all':
        return  get_WS353_all()
    elif dataset == 'WS353_relatedness':
        return  get_WS353_relatedness()
    elif dataset == 'WS353_similarity':
        return  get_WS353_similarity()
    elif dataset == 'WS353_set1':
        return  get_WS353_set1()
    elif dataset == 'WS353_set2':
        return  get_WS353_set2()
    elif dataset == 'RG65':
        return  get_RG65()
    elif dataset == 'RW':
        return  get_RW()
    elif dataset == 'VERB-143':
        return  get_Verb143()
    elif dataset == 'MC-30':
        return  get_MC30()
    elif dataset == 'YP-130':
        return  get_YP130()
    elif dataset == 'SimVerb-3500':
        return  get_SimVerb3500()
    elif dataset == 'SimLex999':
        return  get_SimLex999()
    else:
        raise ValueError("The dataset {} is not supported".format(dataset))
    
def evaluate_in_dataset(dataset,emb,backoff_embs=None,formatemb="text", normalize=True, to_unicode=True, lower=True, path2='', lowercase_dataset = False):
    
    data = get_dataset(dataset)
    if isinstance(emb, str):
        emb = load_embedding(emb, format=formatemb, vocabulary = set(np.append((data.X[:,0]),(data.X[:,1]))), normalize=normalize, to_unicode=to_unicode, lower=lower, path2=path2)
    
    return similarity_emd(emb, data.X, data.y, backoff_embs,lowercase_dataset)



def evaluate_in_dataset_avg(dataset, embs, weigths, lowercase_dataset=False):
    data = get_dataset(dataset)
    return average_similarity(embs, data.X, data.y, weights,lowercase_dataset)



    
def evaluate_on_all(emb,backoff_embs=None,formatemb="text", normalize=True, to_unicode=True, lower=True, path2='',lowercase_dataset=False):
    result = []
    
    if isinstance(emb, str):
        emb = load_embedding(emb, format=formatemb, vocabulary = get_vocab_all(), normalize=normalize, to_unicode=to_unicode, lower=lower, path2=path2)
    
    for name, data in iteritems(datasets):
        d = {'dataset':name}
        d.update(similarity_emd(emb, data.X, data.y, backoff_embs,lowercase_dataset))
        result = np.append(result, d)
    
    return result



def evaluate_on_all_avg(embs, weights=None,lowercase_dataset=False):
    result = []
    for name, data in iteritems(datasets):
        d = {'dataset':name}
        d.update(average_similarity(embs, data.X, data.y, weights,lowercase_dataset))
        result = np.append(result, d)
        
    return result


def results_to_csv(res, correlation='spearman', printRes=True, returnRes=False):
    assert correlation in ["spearman","pearson"], "Unrecognized Correlation method"
    txtRest= ''
    txtCov = ''
    for y in res:
        txtRest = txtRest + str(y[correlation]) + ','
        txtCov = txtCov + str(y['coverage']) + ','
    
    if printRes:
        print(txtRest)
        print(txtCov)
    if returnRes:
        return txtRest,txtCov
    
def export_to_csv(txtResults,txtCov,name=None, filenameResults = 'Results.csv', filenameCoverage = 'Coverage.csv',delimiter=","):
    if name:
        txtResults = str(name)+ ","+ txtResults
        txtCov = str(name)+"," + txtCov
    
    
    with open(filenameResults, 'a+') as file:
        print('%s' % (str(txtResults)), file=file)
        
    with open(filenameCoverage, 'a+') as file:
        print('%s' % (str(txtCov)), file=file)
    
        
    
        
    

In [7]:
from tqdm import tqdm
from annoy import AnnoyIndex
#import knn
#https://github.com/chrischoy/knn_cuda
#def k_nearest_GPU(emb,vector,k=10):
#    return knn.knn(emb.vectors, vector, k)

#https://github.com/spotify/annoy
def k_nearest_annoy(u,vector,k=10):
    return u.get_nns_by_vector(vector,k)

    
def generate_annoy(emb):
    t = AnnoyIndex(emb.dims)
    for i in tqdm(range(len(emb.words))):
        t.add_item(i,emb.vectors[i])
    t.build(10)
    
    return t

def nearest_cosine(emb,vector,k):
    nearest = sorted(emb.words,key= lambda w: calculate_cosine_simil(vector,emb.word_to_vector(w)), reverse=True)
    return nearest[0:k]

    

        

In [ ]:
vec = N2.word_to_vector('03629986-n')
print(vec[0:2])

In [ ]:
nearest_cosine(N1,vec,10)

In [ ]:
t = generate_annoy(N1)

In [ ]:
i = k_nearest_annoy(t,vec)
for ind in i:
    print(N1.words[ind]+",")

In [ ]:
N1 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/UKBrm.Synset-UKBr.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#N2 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/Synset.Synset-UKBr.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)


In [ ]:
import time
start_time = time.time()
print(get_top_cosine_sort(N1.word_to_vector('cat'),N1,N1.words,10))
print("--- %s seconds ---" % (time.time() - start_time))


In [ ]:
start_time = time.time()
print(get_top_cosine(N1.word_to_vector('cat'),N1,10,N1.words))
print("--- %s seconds ---" % (time.time() - start_time))

In [ ]:
t = generate_annoy(N1)

In [ ]:
start_time = time.time()
print(k_nearest_annoy(t,N1,N1.word_to_vector('cat'),k=10))
print("--- %s seconds ---" % (time.time() - start_time))

In [ ]:
def cos_cdist(matrix, vector):
    """
    Compute the cosine distances between each row of matrix and vector.
    """
    v = vector.reshape(1, -1)
    #print(v)
    return 1 - scipy.spatial.distance.cdist(matrix, v, 'cosine').reshape(-1)

start_time = time.time()
cos = cos_cdist(N1.vectors,N1.word_to_vector('cat'))
index =  get_largest_index(cos,10)

top = []
for i in index:
    top.append(N1.words[i])

print(top)
    

print("--- %s seconds ---" % (time.time() - start_time))

In [ ]:
u = set(generate_overlapping_vocab([N1,N2]))

In [ ]:
a = generate_annoy_embeddings([N1,N2], u)

In [ ]:
annoy_array[0].get_nns_by_vector(N2.word_to_vector('cat'),10)

In [ ]:
k_nearest_annoy(a[0],N2,N2.word_to_vector('door'),10)

In [ ]:
index =  a[1].get_nns_by_vector(N2.word_to_vector('door'),10)

In [ ]:


for emb in [N1,N2]:
    vectors = []
    for w in tqdm(u):
        vectors.append(emb.word_to_vector(w))
    
    

In [ ]:
from heapq import nlargest
n = nlargest(10, enumerate(cos), key=lambda x: x[1])
res_list = [x[0] for x in n]
res_list

In [ ]:
calculate_cosine_for_list(N1.word_to_vector('cat'),N1,N1.words)

In [ ]:
calculate_cosine_simil(N1.word_to_vector('cat'),N1.vectors[1])

In [8]:
#New_emb_Combinations.py
from tqdm import tqdm
import numpy as np
from joblib import Parallel, delayed
import multiprocessing
from heapq import nlargest
from tqdm import tqdm
from sklearn.preprocessing import normalize
from annoy import AnnoyIndex

def normalize_vector(vector,norm='l2'):
    vector = np.asarray(vector).reshape(-1,len(vector))
    return normalize(vector,norm=norm)[0]

def generate_overlapping_vocab(embs):
    vocab = set(embs[0].words)
    for i in range(1,len(embs)):
        vocab = vocab.intersection(embs[i].words)
    return list(vocab)
    #return set(embs[0].words).intersection(*embs.words)

    
def calculate_cosine_for_list(vector, emb, overlap_vocab):    
    #start_time = time.time()
    f = lambda w: calculate_cosine_simil(vector,emb.word_to_vector(w))
    return np.fromiter((f(xi) for xi in overlap_vocab), vector.dtype, count=len(overlap_vocab))

    
    
def get_largest_index(list_cos,k):
    n = nlargest(k, enumerate(list_cos), key=lambda x: x[1])
    return  [x[0] for x in n]


def get_top_cosine(vector,emb,k=10,overlap_vocab=None):
    if overlap_vocab is None:
        overlap_vocab = emb.words
        logging.warning('No overlapping vocabulary, using the vocabulary of the embedding')
    
    cos = calculate_cosine_for_list(vector, emb, overlap_vocab)
    index =  get_largest_index(cos,k)
    
    del cos
    top = []
    for i in index:
        top.append(overlap_vocab[i])
    return top
    

def get_top_cosine_sort(vector,emb,overlap_vocab,k=10):
    nearest = sorted(emb.words,key= lambda w: calculate_cosine_simil(vector,emb.word_to_vector(w)), reverse=True)
    
    top = []
    i = 0
    while len(top)<k & i<len(nearest):
        if nearest[i] in overlap_vocab:
            top.append(nearest[i])
        i += 1
    return top


def cos_cdist(matrix, vector):
    v = vector.reshape(1, -1)
    return 1 - scipy.spatial.distance.cdist(matrix, v, 'cosine').reshape(-1)


def get_top_cosine_scipy(vector,emb,k=10,overlap_vocab=None, overlap_matrix = None):
    if overlap_vocab is None:
        overlap_vocab = emb.words
        overlap_matrix = emb.vectors
        logging.warning('No overlapping vocabulary, using the vocabulary of the embedding')
        
    cos = cos_cdist(overlap_matrix,vector)
    index =  get_largest_index(cos,k)

    top = []
    for i in index:
         top.append(overlap_vocab[i])
    return top
    
    
    

def k_nearest_annoy(u,emb,vector,k=10):
    index =  u.get_nns_by_vector(vector,k)
    return [emb.words[x] for x in index]
    
def generate_annoy(emb):
    t = AnnoyIndex(emb.dims)
    for i in tqdm(range(len(emb.words))):
        t.add_item(i,emb.vectors[i])
    t.build(10)
    
    return t

def generate_annoy_embeddings(embs, overlapping_vocab):
    annoy_array = []
    
    for emb in embs:
        t = AnnoyIndex(emb.dims)
        for num, w in enumerate(emb.words):
            if w in overlapping_vocab:
                t.add_item(num,emb.vectors[num])
        t.build(10)
        annoy_array.append(t)
        
    return annoy_array


def generate_overlapping_matrix(overlapping_vocab,emb):
    matrix = []
    for w in overlapping_vocab:
        matrix.append(emb.word_to_vector(w))
        #matrix = np.append(matrix,emb.word_to_vector(w),axis=0)
    return matrix

def generate_overlapping_matrix_embs(overlapping_vocab,embs):
    over = []
    for e in embs:
        over.append(generate_overlapping_matrix(overlapping_vocab,e))
    return over

def generate_word(embedding,list_embs,word,overlapping_vocab=None,overlapping_matrix=None, annoy = None, number_of_words = 10, method = 'cosine'):
    assert method in ["cosine","knearest"], "Concatenate: Unrecognized method"
    
    if overlapping_vocab is None:
        overlapping_vocab = generate_overlapping_vocab(list_embs)
    
    if overlapping_matrix is None:
        overlapping_matrix = generate_overlapping_matrix_embs(overlapping_vocab,list_embs)
    
    #if method == 'cosine':
    #    overlapping_vocab = overlapping_vocab
    #else: 
    #    overlapping_vocab = overlapping_vocab

    if len(overlapping_vocab) == 0:
        raise ValueError("There are no overlapping words between the embeddings")
        
    if method == 'knearest': 
        if annoy is None:
            annoy = generate_annoy_embeddings(list_embs,overlapping_vocab)
    
        
    
    #else:
    #    if annoy is None:
    #        annoy=[]
    #        for emb in list_embs:
    #            annoy.append(generate_annoy(emb))
    #            
    #    if len(annoy) != len(list_embs):
    #        raise ValueError('We need the same number of annoy indexes than embeddings')
    
    
    
    
    #Search a vector for the word (We will use the first embedding that contains the word)
    vector = None
    emb_n = None
    emb_u = None
    
    for e_num, e in enumerate(list_embs):
        try:
            vector = e.word_to_vector(word)
            emb_n = e
            emb_u = e_num
            break
        except KeyError as err:
            continue
    
    if vector is None:
        logging.warning("Word {} not found in any embedding.".format(word))
        return None
    
    if method == 'cosine':
        #top = get_top_cosine(vector,emb_n,number_of_words,overlapping_vocab)
        
        #return vector, emb_n, number_of_words, overlapping_vocab, overlapping_matrix[emb_u]
        #print('VECTOR:')
        #print(vector)
        #print('emb_n')
        #print(emb_n)
        top = get_top_cosine_scipy(vector,emb_n,number_of_words,overlapping_vocab,overlapping_matrix[emb_u])
    else:
        top = k_nearest_annoy(annoy[emb_u],emb_n,vector,number_of_words)
    
    if len(top)<number_of_words:
        logging.warning("Not enough words to generate a vector for the word {}, consider to modify the number_of_words parameter. Note: The vector will be generated with the available words".format(word))
    #print('W: ')
    #print(word)
    #print('TOP:')
    #print(top)
    result = np.zeros(embedding.dims, dtype=np.float32)
    
    for w in top:
        result+=embedding.word_to_vector(w)
    
    
    
    return result/len(top)
        


    
def get_vector_concat(embs, word,weights=None, method="zeros",overlapping_vocab = None, overlapping_matrix = None, annoy=None,k=10, method_generate = 'cosine', normalize=False):
    vector = []
    for e in range(len(embs)):
        try:
            if weights is None:
                if normalize:
                    vector = np.append(vector,normalize_vector(embs[e].word_to_vector(word)),axis=0)
                else:  
                    vector = np.append(vector,embs[e].word_to_vector(word),axis=0)
                
            else:
                if normalize:
                    vector = np.append(vector,normalize_vector(embs[e].word_to_vector(word))*weights[e],axis=0)
                else:
                    vector = np.append(vector,embs[e].word_to_vector(word)*weights[e],axis=0)
        except KeyError as err:
            if method == "zeros":
                vector = np.append(vector,np.zeros(shape=(embs[e].dims),dtype=np.float32))
                
            elif method == "generate":
                vector_gen = generate_word(embs[e],embs,word,overlapping_vocab,overlapping_matrix, annoy,k,method_generate)
                if vector_gen is None:
                    logging.warning("Word {} omitted.".format(word))
                    return None
                else: 
                    #logging.warning("Vector generated for the word {}".format(word))
                    if weights is None:
                        if normalize:
                            vector = np.append(vector,normalize_vector(vector_gen),axis=0)
                        else:  
                            vector = np.append(vector,vector_gen,axis=0)
                
                    else:
                        if normalize:
                            vector = np.append(vector,normalize_vector(vector_gen)*weights[e],axis=0)
                        else:
                            vector = np.append(vector,vector_gen*weights[e],axis=0)
    
            else:
                return None
    
    return vector

def get_vector_avg(embs,word,weights=None,method="ignore",overlapping_vocab = None, overlapping_matrix = None, annoy=None,k=10, method_generate = 'cosine', normalize=False, norm='l1'):
    div = 0
    avg = np.zeros(embs[0].dims, dtype=np.float32)

    for e in range(len(embs)):
        try:
            if weights is None:
                if normalize:
                    avg+=normalize_vector(embs[e].word_to_vector(word),norm)
                else:
                    avg+=embs[e].word_to_vector(word)
                div += 1
            else:
                if normalize:
                    avg+=normalize_vector(embs[e].word_to_vector(word),norm) * weights[e]
                else:
                    avg+=embs[e].word_to_vector(word) * weights[e]
                div+=weights[e]
            
        except KeyError as err:
            if method == "skip":
                return None
            elif method=="generate":
                vector_gen = generate_word(embs[e],embs,word,overlapping_vocab,overlapping_matrix,annoy,k,method_generate)
                if vector_gen is None:
                    logging.warning("Word {} omitted.".format(word))
                    return None
                else:
                    #logging.warning("Vector generated for the word {}".format(word))
                    
                    if weights is None:
                        if normalize:
                            avg+=normalize_vector(vector_gen,norm)
                        else:
                            avg+=vector_gen
                        div += 1
                    else:
                        if normalize:
                            avg+=normalize_vector(vector_gen,norm) * weights[e]
                        else:
                            avg+=vector_gen * weights[e]
                        div+=weights[e]
              
            else:
                continue

    if (div > 0):
        return avg/div

    else:
        logging.warning("Word {} not found in any embedding.".format(word))
        return None
    
                    
def concatenate_embeddings(embs, path='/home/concat.vec', vocabulary = None, weights=None, method="zeros",generate_method='cosine',k=10,normalize=False,where="file"):
    assert method in ["zeros","skip","generate"], "Concatenate: Unrecognized method"
    assert generate_method in ["cosine","knearest"], "Concatenate: Unrecognized generation method"
    assert where in ["file","return","generate"], "Concatenate: Unrecognized return method"
    
    if vocabulary is None: 
        vocabulary = set()
        for e in embs:
            for w in e.words:
                vocabulary.add(w)
                
    
    else:
        if len(set(vocabulary)) != len(vocabulary):
            logging.warning("Provided vocabulary has duplicates. IMPORTANT NOTE: The new embedding WILL HAVE duplicates, you may want to check your vocabulary")
    
    annoy = None
            
    if method == "generate":
        overlapping_vocab = generate_overlapping_vocab(embs)
        if generate_method == 'knearest':
            annoy = generate_annoy_embeddings(embs,overlapping_vocab)
            overlapping_matrix = None
        else: 
            annoy = None
            overlapping_matrix = generate_overlapping_matrix_embs(overlapping_vocab,embs)
    else:
        overlapping_vocab = None
        overlapping_matrix = None
 
    
    num_words = 0
    word_ignored = 0
    len_vectors = 0
    
    for e in embs:
        len_vectors+=e.dims
        
    if where == "file":
        with open(path, 'w') as file:
            for w in tqdm(vocabulary):
                v = get_vector_concat(embs,w,weights,method,overlapping_vocab,overlapping_matrix,annoy,k,generate_method,normalize)
                if v is not None:
                    print(w + ' ' +' '.join(['%.6g' % x for x in v] ), file=file)
                    num_words+=1
                else:
                    word_ignored+=1
                    logging.warning("Word {} ignored".format(w))
    
    else:
        vocab = []
        vectors = []
        for w in tqdm(vocabulary):
            v = get_vector_concat(embs,w,weights,method,overlapping_vocab,overlapping_matrix,annoy,k,generate_method,normalize)
            if v is not None:
                vocab.append(w)
                vectors.append(v)
                num_words+=1
            else:
                word_ignored+=1
                logging.warning("Word {} ignored".format(w))
            
    if word_ignored > 0:
        logging.warning("Ignored {} words of the combined vocabulary between the embeddings".format(word_ignored))
    

    
    logging.getLogger().setLevel(logging.INFO)
    logging.info("The new embedding has {} word and vectors have {} dimensions".format(num_words,len_vectors))
    
    if where  == "file":
        return True
    
    return Embedding(vocabulary=Vocabulary(words=vocab, lower = False), vectors=vectors)
    
def avg_embeddings(embs, path='/home/avg.vec', vocabulary = None, weights=None, method = "ignore",generate_method='cosine',k=10,normalize=False, normalize_norm='l2', where="file"):
    assert method in ["skip","ignore","generate"], "Average: Unrecognized method"
    assert where in ["file","return"], "Average: Unrecognized return method"
        
    dims = embs[0].dims
    for e in embs:
        if e.dims!=dims:
            raise ValueError("All the embedding must have the same vector length. Found and embedding with {} dimensions and another one with {} dimensions".format(dims,e.dims))
    
    
    if vocabulary is None: 
        vocabulary = []
        for e in embs:
            vocabulary= np.append(vocabulary,e.words, axis=0)
        vocabulary = set(vocabulary)
    
    else:
        if len(set(vocabulary)) != len(vocabulary):
            logging.warning("Provided vocabulary has duplicates. IMPORTANT NOTE: The new embedding WILL HAVE duplicates, you may want to check your vocabulary")
    
    annoy = None
    
    if method == "generate":
        overlapping_vocab = generate_overlapping_vocab(embs)
        if generate_method == 'knearest':
            annoy = generate_annoy_embeddings(embs,overlapping_vocab)
            overlapping_matrix = None
        else: 
            annoy = None
            overlapping_matrix = generate_overlapping_matrix_embs(overlapping_vocab,embs)
    else:
        overlapping_vocab = None
        overlapping_matrix = None

    
    num_words = 0
    word_ignored= 0
    
    if where == "file":
    
        with open(path, 'w') as file:
            for w in tqdm(vocabulary):

                r = get_vector_avg(embs,w,weights,method,overlapping_vocab,overlapping_matrix,annoy,k,generate_method,normalize,normalize_norm)
                if r is not None:
                    print(w + ' ' +' '.join(['%.6g' % x for x in r] ), file=file)
                    num_words+=1
                else:
                    word_ignored+=1
                    logging.warning("Word {} ignored".format(w))
    else:
        vocab = []
        vectors = []
        for w in tqdm(vocabulary):
            r = get_vector_avg(embs,w,weights,method,overlapping_vocab,overlapping_matrix,annoy,k,generate_method,normalize,normalize_norm)
            if r is not None:
                vocab.append(w)
                vectors.append(r)
                num_words+=1
            else:
                word_ignored+=1
                logging.warning("Word {} ignored".format(w))

            
    if word_ignored > 0:
        logging.warning("Ignored {} words of the combined vocabulary between the embeddings".format(word_ignored))
    

    
    logging.getLogger().setLevel(logging.INFO)
    logging.info("The new embedding has {} words and vectors have {} dimensions".format(num_words,dims))
    
    if where  == "file":
        return True
    
    return Embedding(vocabulary=Vocabulary(words=vocab, lower = False), vectors=vectors)


def generate_dictionary_for_vecmap(emb1, emb2, path, return_dict = False):
    vocab1 = emb1.words
    vocab2 = emb2.words
    
    dictionary = set(vocab1).intersection(vocab2)
    
    with open(path, 'w') as file:
        for w in tqdm(dictionary):
            print(w + ' ' + w, file = file)
    
    if return_dict:
        return dictionary
    
    return True
    
def generate_dictionary_vecmap_top_words(infile,outfile,frequency=False):
    
    with open(infile) as f:
        if not frequency:
            words = f.read().splitlines('\t')
        else:
            words = []
            for line in f:
                words.append(line.split()[0])
            
    with open(outfile, 'w') as file:
        for w in tqdm(words):
            print(w + ' ' + w, file = file)
            
    return True


def generate_dictionary_emb_synset(infile,outfile):
    
    words = []
    sysets = []
    
    with open(infile) as f:
        for line in f:
            w = line.split()
            if len(w)==2:
                words.append(w[0])
                sysets.append(w[1][0:-2])
    with open(outfile, 'w+') as file:
        for w in tqdm(range(len(words))):
            print(words[w] + ' ' + sysets[w], file = file)
            
    return True

In [9]:
import multiprocessing
import os

global list_embs
global overlapping_vocab
global list_vocabulary
global list_weights
global method_avg
global list_annoy
global k_avg
global generate_method_avg
global overlapping_matrix
import time
import datetime


def avg_batch_file(path,first,last):
    
    global list_embs
    global overlapping_vocab
    global list_vocabulary
    global list_weights
    global method_avg
    global list_annoy
    global k_avg
    global generate_method_avg
    global overlapping_matrix
    with open(path, 'w') as file:
        start_time = time.time()
        for i in range(first,last):
            r = get_vector_avg(list_embs,list_vocabulary[i],list_weights,method_avg,overlapping_vocab,overlapping_matrix,list_annoy,k_avg,generate_method_avg)
            if r is not None:
                print(list_vocabulary[i] + ' ' +' '.join(['%.6g' % x for x in r] ), file=file)
            #else:
            #    word_ignored+=1
            #    logging.warning("Word {} ignored".format(list_vocabulary[i]))
            
            if i%100==0:
                print("Thread" + str(multiprocessing.current_process()) + ": " + str(i-first) + " of " + str(last-first) + " Time remaining: " + str(datetime.timedelta(seconds=(time.time() - start_time)/100*(last-i))))
                start_time = time.time()




def avg_embeddings_generate_multithread(embs, path='/home/avg', vocabulary = None, weights=None, method = "ignore",generate_method='cosine',k=10):
    global list_embs
    global overlapping_vocab
    global list_vocabulary
    global list_weights
    global method_avg
    global list_annoy
    global k_avg
    global generate_method_avg
    global overlapping_matrix

    
    assert method in ["skip","ignore","generate"], "Average: Unrecognized method"
        
    dims = embs[0].dims
    for e in embs:
        if e.dims!=dims:
            raise ValueError("All the embedding must have the same vector length. Found and embedding with {} dimensions and another one with {} dimensions".format(dims,e.dims))
    
    
    if vocabulary is None: 
        vocabulary = []
        for e in embs:
            vocabulary= np.append(vocabulary,e.words, axis=0)
        vocabulary = set(vocabulary)  
    else:
        if len(set(vocabulary)) != len(vocabulary):
            logging.warning("Provided vocabulary has duplicates. IMPORTANT NOTE: The new embedding WILL HAVE duplicates, you may want to check your vocabulary")  
    
    if method == "generate":
        overlapping_vocab = generate_overlapping_vocab(embs)
        if generate_method == 'knearest':
            annoy = generate_annoy_embeddings(embs,overlapping_vocab)
            overlapping_matrix = None
        else: 
            annoy = None
            overlapping_matrix = generate_overlapping_matrix_embs(overlapping_vocab,embs)
    else:
        overlapping_vocab = None
        
    list_vocabulary = list(vocabulary)
    list_embs = embs
    list_weights = weights
    method_avg = method
    list_annoy = annoy
    k_avg = k
    generate_method_avg = generate_method

    
    CPUs= multiprocessing.cpu_count()-1
    
    batch = int(len(vocabulary)/CPUs)
    batch_start = 0
    batch_end = batch_start + batch
    
    
    
    for process_idx in range(CPUs):
        if process_idx ==  CPUs-1:
            batch_end = len(vocabulary)
            
        name = path+str(process_idx)
        
        p = multiprocessing.Process(target=avg_batch, args=(name,batch_start,batch_end,))
        os.system("taskset -p -c %d %d" % (process_idx % CPUs, os.getpid()))
        p.start()
        batch_start = batch_end
        batch_end = batch_end + batch
        

        
        
        
        

                          
    
    
    

In [10]:
global embp
global list_embs
global overlapping_vocab
global list_vocabulary
global method_gen
global list_annoy
global k_gen
global overlapping_matrix



def generate_batch(path,first,last):
    global embp
    global list_embs
    global overlapping_vocab
    global list_vocabulary
    global method_gen
    global list_annoy
    global k_gen
    global overlapping_matrix
    
    with open(path, 'w') as file:
        start_time = time.time()
        for i in range(first,last):
            try:
                vector = embp.word_to_vector(list_vocabulary[i])
            
            except KeyError as err:
                vector = generate_word(embp,list_embs,list_vocabulary[i],overlapping_vocab,overlapping_matrix,list_annoy,k_gen,method_gen) 
            
            if vector is not None:
                print(list_vocabulary[i] + ' ' +' '.join(['%.6g' % x for x in vector] ), file=file)
            else:
                logging.warning("Word {} ignored".format(list_vocabulary[i]))
                
            if i%100==0:
                print("Thread" + str(multiprocessing.current_process()) + ": " + str(i-first) + " of " + str(last-first) + " Time remaining: " + str(datetime.timedelta(seconds=(time.time() - start_time)/100*(last-i))))
                start_time = time.time()
        
def merge_vocab_generator(emb,embs,path,vocab=None, method = 'cosine', k = 10):
    global embp                    
    global list_embs
    global overlapping_vocab
    global list_vocabulary
    global method_gen
    global list_annoy
    global k_gen
    global overlapping_matrix                          

    embs.append(emb)
    
    if vocab is None: 
        vocab = []
        for e in embs:
            vocab= np.append(vocab,e.words, axis=0)
        vocab = set(vocab)  
    
    
    overlapping_vocab = generate_overlapping_vocab(embs)
    
    
    if method == 'cosine':
        overlapping_matrix = generate_overlapping_matrix_embs(overlapping_vocab,embs)
    else:
        overlapping_matrix = None
    
    if method == 'knearest':
        annoy = generate_annoy_embeddings(embs,overlapping_vocab)
    else:
        annoy = None
    
    embp = emb                    
    list_embs = embs
    
    list_vocabulary = list(set(vocab))
    method_gen = method
    list_annoy = annoy
    k_gen = k
    overlapping_matrix = overlapping_matrix
    
    CPUs= multiprocessing.cpu_count()-1
    
    batch = int(len(list_vocabulary)/CPUs)
    batch_start = 0
    batch_end = batch_start + batch
    
    
    
    for process_idx in range(CPUs):
        if process_idx ==  CPUs-1:
            batch_end = len(list_vocabulary)
            
        name = path+str(process_idx)
        
        p = multiprocessing.Process(target=generate_batch, args=(name,batch_start,batch_end,))
        os.system("taskset -p -c %d %d" % (process_idx % CPUs, os.getpid()))
        p.start()
        batch_start = batch_end
        batch_end = batch_end + batch                  

                    
                        

In [11]:
generate_dictionary_emb_synset('/home/iker/Escritorio/wnet30_dict.txt','/home/iker/Escritorio/wnet30_dict_filtered.txt')

100%|██████████| 120433/120433 [00:00<00:00, 771821.71it/s]


True

In [12]:
#auto_eval_scrips.py
from copy import deepcopy
import itertools
import datetime
import psutil
import sys
import os

def test_normalization(path,embformat='txt', dims_restriction = None, delete_duplicates = False, lowercase_datasets=False):
    E = load_embedding(path, format=embformat, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, dims_restriction=dims_restriction, delete_duplicates = delete_duplicates)
    
    print('============ORIGINAL==========')
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    

    print('============Mean center EMB==========')
    E.mean_center_embeddingwise()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))

    del E
    
    print('============L1 por columnas==========')
    E = load_embedding(path, format=embformat, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, dims_restriction=dims_restriction, delete_duplicates = delete_duplicates)
    E.L1_dimensionwwise()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    del E
    
    
    E = load_embedding(path, format=embformat, vocabulary = None, length_normalize = True, normalize_dimensionwise=False, dims_restriction=dims_restriction, delete_duplicates = delete_duplicates)
    originalmatrix = deepcopy(E.vectors)
    
    print('============L2 rowwise + Mean Center==========')
    E.mean_center()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============L2 rowwise + PPA==========')
    del E.vectors
    E.vectors = deepcopy(originalmatrix)
    E.vectors = PPA(E.vectors)
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============L2 rowwise + L2 dimensionwise==========')
    del E.vectors
    E.vectors = deepcopy(originalmatrix)
    E.length_normalize_dimensionwise()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============L2 rowwise + L2 dimensionwise + PPA==========')
    del E.vectors
    E.vectors = deepcopy(originalmatrix)
    E.length_normalize_dimensionwise()
    E.vectors = PPA(E.vectors)
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    del originalmatrix
    del E
    
    E = load_embedding(path, format=embformat, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, dims_restriction=dims_restriction, delete_duplicates = delete_duplicates)
    originalmatrix = deepcopy(E.vectors)
    
    print('============L2 dimensionwise==========')
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============L2 dimensionwise + Mean Center==========')
    E.mean_center()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============L2 dimensionwise + PPA==========')
    del E.vectors
    E.vectors = deepcopy(originalmatrix)
    E.vectors = PPA(E.vectors)
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    del originalmatrix
    del E
    
    E = load_embedding(path, format=embformat, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, dims_restriction=dims_restriction, delete_duplicates = delete_duplicates)
    E.mean_center()
    originalmatrix = deepcopy(E.vectors)
    
    print('============Mean center==========')
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============ Mean Center + L2 dimensionwise ==========')
    E.length_normalize_dimensionwise()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============Mean Center + PPA==========')
    del E.vectors
    E.vectors = deepcopy(originalmatrix)
    E.vectors = PPA(E.vectors)
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============ Mean Center + L2 rowwise + L2 dimensionwise ==========')
    del E.vectors
    E.vectors = deepcopy(originalmatrix)
    E.length_normalize()
    E.length_normalize_dimensionwise()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    del originalmatrix
    del E
    
    E = load_embedding(path, format=embformat, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, dims_restriction=dims_restriction, delete_duplicates = delete_duplicates)
    E.vectors = PPA(E.vectors)
    originalmatrix = deepcopy(E.vectors)
    
    print('============ PPA  ==========')
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============ PPA + L2 dimensionwise ==========')
    E.length_normalize_dimensionwise()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============ PPA + Mean Center ==========')
    del E.vectors
    E.vectors = deepcopy(originalmatrix)
    E.mean_center()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    print('============ PPA + L2 rowwise + L2 dimensionwise ==========')
    del E.vectors
    E.vectors = deepcopy(originalmatrix)
    E.length_normalize()
    E.length_normalize_dimensionwise()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    del originalmatrix
    del E
    print('============ L2 rowwise + L2 dimensionwise + Mean center ==========')
    E = load_embedding(path, format=embformat, vocabulary = None, length_normalize = True, normalize_dimensionwise=True, dims_restriction=dims_restriction, delete_duplicates = delete_duplicates)
    E.mean_center()
    results_to_csv(evaluate_on_all(E,lowercase_dataset=lowercase_datasets))
    
    del E
    
    return True


def test_similarity_auto(embs,names,w):
    t = ''
    for n in range(len(names)):
        if n == len(names)-1:
             t = t+','+str(names[n])
        else:
            if n==0:
                t = str(names[n])
            else:
                t = t+'+'+str(names[n])
        
    a,b = results_to_csv(evaluate_on_all_avg(embs,lowercase_dataset=True,weights=np.array(w)),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=str(t))

    
def test_concatenate_auto(embs,names,w,normalize=True):
    t = ''
    for n in range(len(names)):
        if n == len(names)-1:
             t = t+','+str(names[n])
        else:
            if n==0:
                t = str(names[n])
            else:
                t = t+'+'+str(names[n])
    
    
    c = concatenate_embeddings(embs, path='/home/concat.vec', vocabulary = dataset_min, weights=np.array(w), method="generate",generate_method='cosine',k=10,normalize=True,where="return")
    a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=str(t), filenameResults = 'L2Concat_REDO.csv', filenameCoverage = 'L2ConcatCoverage_REDO.csv')
    
    del c
    
    c = concatenate_embeddings(embs, path='/home/concat.vec', vocabulary = dataset_min, weights=np.array(w), method="generate",generate_method='cosine',k=10,normalize=False,where="return")
    a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=str(t), filenameResults = 'Concat_REDO.csv', filenameCoverage = 'ConcatCoverage_REDO.csv')

    
    
def test_average_auto(embs,names,w,normalize=True):
    t = ''
    for n in range(len(names)):
        if n == len(names)-1:
             t = t+','+str(names[n])
        else:
            if n==0:
                t = str(names[n])
            else:
                t = t+'+'+str(names[n])
    
    c = avg_embeddings(embs, path='/home/concat.vec', vocabulary = dataset_min, weights=np.array(w), method="generate",generate_method='cosine',k=10,normalize=True,where="return")
    a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=str(t), filenameResults = 'L2AVG_REDO.csv', filenameCoverage = 'L2AVGCoverage_REDO.csv')
    del c
    
    c = avg_embeddings(embs, path='/home/concat.vec', vocabulary = dataset_min, weights=np.array(w), method="generate",generate_method='cosine',k=10,normalize=False,where="return")
    a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=str(t), filenameResults = 'AVG_REDO.csv', filenameCoverage = 'AVGCoverage_REDO.csv')

    
def test_similarity_avg():
    dataset_vocab = get_vocab_simil_all()
    dataset_min = get_vocab_simil_all(True)
    
    
    GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
    W2V = load_embedding(W2V_path, vocabulary = dataset_min, format='bin', length_normalize = False, normalize_dimensionwise=False)
    FT = load_embedding(FastText_CC_path, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    UKB = load_embedding(UKB_path, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    LEXVEC = load_embedding(lexvec, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    SKE = load_embedding(SketchEngine_web_path, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)
    PDC = load_embedding(PDC_path, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    
    embs = [GLOVE,W2V,FT,jointcHYB,UKB,LEXVEC,SKE,PDC]
    names = ['GLOVE','W2V','FT','jointcHYB','UKB','LEXVEC','SKE','PDC']
    
    #De dos en dos
    
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            
            test_similarity_auto([embs[x],embs[y]],[names[x],names[y],'"[1,1]"'],[1,1])
            test_similarity_auto([embs[x],embs[y]],[names[x],names[y],'"[2,1]"'],[2,1])
            test_similarity_auto([embs[x],embs[y]],[names[x],names[y],'"[1,2]"'],[1,2])
            
    #De tres en 3
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                w=[1,1,1]
                test_similarity_auto([embs[x],embs[y],embs[j]],[names[x],names[y],names[j],'"'+str(np.array(w))+'"'],w)
                
                for w in list(itertools.permutations([1, 2, 3])):
                    test_similarity_auto([embs[x],embs[y],embs[j]],[names[x],names[y],names[j],'"'+str(np.array(w))+'"'],w)
                
                for w in list(itertools.permutations([2, 1, 1])):
                    test_similarity_auto([embs[x],embs[y],embs[j]],[names[x],names[y],names[j],'"'+str(np.array(w))+'"'],w)
                
                for w in list(itertools.permutations([3, 1, 1])):
                    test_similarity_auto([embs[x],embs[y],embs[j]],[names[x],names[y],names[j],'"'+str(np.array(w))+'"'],w)
                
                for w in list(itertools.permutations([2, 2, 1])):
                    test_similarity_auto([embs[x],embs[y],embs[j]],[names[x],names[y],names[j],'"'+str(np.array(w))+'"'],w)
    
    #de 4 en 4
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    w = [1,1,1,1]
                    test_similarity_auto([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z],'"'+str(np.array(w))+'"'],w)
                    for w in list(itertools.permutations([1, 2, 3, 4])):
                        test_similarity_auto([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z],'"'+str(np.array(w))+'"'],w)

                    for w in list(itertools.permutations([3, 1, 1, 1])):
                        test_similarity_auto([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z],'"'+str(np.array(w))+'"'],w)
                    
                    for w in list(itertools.permutations([2, 1, 1, 1])):
                        test_similarity_auto([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z],'"'+str(np.array(w))+'"'],w)
                    
                    for w in list(itertools.permutations([2, 2, 1, 1])):
                        test_similarity_auto([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z],'"'+str(np.array(w))+'"'],w)

                   
    #de 5 en 5
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                        w = [1,1,1,1,1]
                        test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v],'"'+str(np.array(w))+'"'],w)
                        for w in list(itertools.permutations([1, 2, 3, 4,5])):
                            test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v],'"'+str(np.array(w))+'"'],w)

                        for w in list(itertools.permutations([3, 1, 1, 1,1])):
                            test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v],'"'+str(np.array(w))+'"'],w)
                        
                        for w in list(itertools.permutations([2, 1, 1, 1,1])):
                            test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v],'"'+str(np.array(w))+'"'],w)
                        
                        for w in list(itertools.permutations([2, 2, 1, 1,1])):
                            test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v],'"'+str(np.array(w))+'"'],w)
                        
                        for w in list(itertools.permutations([3, 2, 2, 1,1])):
                            test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v],'"'+str(np.array(w))+'"'],w)
                            
                        
                    
    #de 6 en 6
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                        for i in range(v+1,len(names)): 
                            w = [1,1,1,1,1,1]
                            test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i],'"'+str(np.array(w))+'"'],w)
                            for w in list(itertools.permutations([1, 2, 3, 4, 5, 6])):
                                test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i],'"'+str(np.array(w))+'"'],w)
                                
                            for w in list(itertools.permutations([3,1, 1, 1, 1,1])):
                                test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i],'"'+str(np.array(w))+'"'],w)
                            
                            for w in list(itertools.permutations([2,1, 1, 1, 1,1])):
                                test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i],'"'+str(np.array(w))+'"'],w)
                            
                            for w in list(itertools.permutations([2, 2, 2, 2, 1,1])):
                                test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i],'"'+str(np.array(w))+'"'],w)
                               
     #de 7 en 7
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                        for i in range(v+1,len(names)): 
                            for t in range(i+1,len(names)): 
                                w = [1,1,1,1,1,1,1]
                                test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i],embs[t]],[names[x],names[y],names[j],names[z],names[v],names[i],names[t],'"'+str(np.array(w))+'"'],w)
                                for w in list(itertools.permutations([1, 2, 3, 4, 5, 6,7])):
                                    test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i],embs[t]],[names[x],names[y],names[j],names[z],names[v],names[i],names[t],'"'+str(np.array(w))+'"'],w)

                                for w in list(itertools.permutations([3,1,1, 1, 1, 1,1])):
                                    test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i],embs[t]],[names[x],names[y],names[j],names[z],names[v],names[i],names[t],'"'+str(np.array(w))+'"'],w)
                                
                                for w in list(itertools.permutations([2,1,1, 1, 1, 1,1])):
                                    test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i],embs[t]],[names[x],names[y],names[j],names[z],names[v],names[i],names[t],'"'+str(np.array(w))+'"'],w)

                                for w in list(itertools.permutations([2,2,2, 2, 1, 1,1])):
                                    test_similarity_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i],embs[t]],[names[x],names[y],names[j],names[z],names[v],names[i],names[t],'"'+str(np.array(w))+'"'],w)

                                
    #Todos
    w = [1,1,1,1,1,1,1,1]
    test_similarity_auto(embs,[names[0],names[1],names[2],names[3],names[4],names[5],names[6],names[7],'"'+str(np.array(w))+'"'],w)
    for w in list(itertools.permutations([1, 2, 3, 4, 5, 6, 7 ,8])):
        test_similarity_auto(embs,[names[0],names[1],names[2],names[3],names[4],names[5],names[6],names[7],'"'+str(np.array(w))+'"'],w)
                           
    for w in list(itertools.permutations([3, 1,1,1, 1, 1, 1,1])):
        test_similarity_auto(embs,[names[0],names[1],names[2],names[3],names[4],names[5],names[6],names[7],'"'+str(np.array(w))+'"'],w)
   
    for w in list(itertools.permutations([2, 1,1,1, 1, 1, 1,1])):
        test_similarity_auto(embs,[names[0],names[1],names[2],names[3],names[4],names[5],names[6],names[7],'"'+str(np.array(w))+'"'],w)
   

    for w in list(itertools.permutations([2, 2,2,2, 1, 1, 1,1])):
        test_similarity_auto(embs,[names[0],names[1],names[2],names[3],names[4],names[5],names[6],names[7],'"'+str(np.array(w))+'"'],w)
   
    for w in list(itertools.permutations([3, 2,2,1,1, 1, 1,1])):
        test_similarity_auto(embs,[names[0],names[1],names[2],names[3],names[4],names[5],names[6],names[7],'"'+str(np.array(w))+'"'],w)
    
    for w in list(itertools.permutations([4, 4,2,2,1, 1, 1,1])):
        test_similarity_auto(embs,[names[0],names[1],names[2],names[3],names[4],names[5],names[6],names[7],'"'+str(np.array(w))+'"'],w)
 





def equal_dims(embs):
    dims = embs[0].dims
    for e in embs:
        if e.dims != dims:
            return False
    return True

def test_concat_avg():        
    dataset_vocab = get_vocab_simil_all()
    dataset_min = get_vocab_simil_all(True)
    
    
    GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
    W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
    FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    SKE = load_embedding(SketchEngine_web_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)
    PDC = load_embedding(PDC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    
    embs = [GLOVE,W2V,FT,jointcHYB,UKB,LEXVEC,SKE,PDC]
    names = ['GLOVE','W2V','FT','jointcHYB','UKB','LEXVEC','SKE','PDC']
    
    #De dos en dos
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            
            test_concatenate_auto([embs[x],embs[y]],[names[x],names[y],'"[1,1]"'],[1,1])
            test_concatenate_auto([embs[x],embs[y]],[names[x],names[y],'"[2,1]"'],[2,1])
            test_concatenate_auto([embs[x],embs[y]],[names[x],names[y],'"[1,2]"'],[1,2])
            test_concatenate_auto([embs[x],embs[y]],[names[x],names[y],'"[8,1]"'],[8,1])
            test_concatenate_auto([embs[x],embs[y]],[names[x],names[y],'"[1,8]"'],[1,8])
            
            if embs[x].dims==embs[y].dims:
                test_average_auto([embs[x],embs[y]],[names[x],names[y],'"[1,1]"'],[1,1])
                test_average_auto([embs[x],embs[y]],[names[x],names[y],'"[2,1]"'],[2,1])
                test_average_auto([embs[x],embs[y]],[names[x],names[y],'"[1,2]"'],[1,2])
    
        #De tres en 3
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                w = [1,1,1]
                test_concatenate_auto([embs[x],embs[y],embs[j]],[names[x],names[y],names[j],'"'+str(np.array(w))+'"'],w)
                
                if equal_dims([embs[x],embs[y],embs[j]]):
                    test_average_auto([embs[x],embs[y],embs[j]],[names[x],names[y],names[j],'"'+str(np.array(w))+'"'],w)
                
    #de 4 en 4
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    w = [1,1,1,1]
                    test_concatenate_auto([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z],'"'+str(np.array(w))+'"'],w)
                    if equal_dims([embs[x],embs[y],embs[j],embs[z]]):
                        test_average_auto([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z],'"'+str(np.array(w))+'"'],w)
                    
                    
                   
    #de 5 en 5
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                        w = [1,1,1,1,1]
                        test_concatenate_auto([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v],'"'+str(np.array(w))+'"'],w)
                        if equal_dims([embs[x],embs[y],embs[j],embs[z],embs[v]]):
                            test_average_auto([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v],'"'+str(np.array(w))+'"'],w)
                         
                    
    #de 6 en 6
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                        for i in range(v+1,len(names)): 
                            w = [1,1,1,1,1,1]
                            test_concatenate_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i],'"'+str(np.array(w))+'"'],w)
                            if equal_dims([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]]):
                                test_average_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i],'"'+str(np.array(w))+'"'],w)
                            
     #de 7 en 7
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                        for i in range(v+1,len(names)): 
                            for t in range(i+1,len(names)): 
                                w = [1,1,1,1,1,1,1]
                                test_concatenate_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i],embs[t]],[names[x],names[y],names[j],names[z],names[v],names[i],names[t],'"'+str(np.array(w))+'"'],w)
                                if equal_dims([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i],embs[t]]):
                                    test_average_auto([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i],embs[t]],[names[x],names[y],names[j],names[z],names[v],names[i],names[t],'"'+str(np.array(w))+'"'],w)
                                 
                                               
                                
    #Todos
    w = [1,1,1,1,1,1,1,1]
    test_concatenate_auto(embs,[names[0],names[1],names[2],names[3],names[4],names[5],names[6],names[7],'"'+str(np.array(w))+'"'],w)

from copy import deepcopy
def test_reduction(embs, name):
    path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/ConcatenatedNoL2/'
    
    path = path + name
    
    c = concatenate_embeddings(embs, path='/home/concat.vec', vocabulary = None, weights=None, method="zeros",generate_method='cosine',k=10,normalize=False, where="return")
    del embs
    
    c.export(path+'.vec')
    
    del c
    
    #original = deepcopy(c)
    
    
    #c.vectors = algo(c.vectors,n)
    #a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    #export_to_csv(txtResults=a, txtCov = b, name=name+'_PPA_'+str(n), filenameResults = 'dim_red', filenameCoverage = 'dim_redCoverage.csv')
    
    
    #del c
    
    #c = deepcopy(original)
    #c.vectors = PCA(c.vectors,n)
    
    #a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    #export_to_csv(txtResults=a, txtCov = b, name=name+'_PCA_'+str(n), filenameResults = 'dim_red', filenameCoverage = 'dim_redCoverage.csv')

    
    #c.export(path+'_PCA_'+str(n))
    
    #del c
    
    #original.vectors = T_SVD(original.vectors,n)
    #original.export(path+'_SVD_'+str(n))
    
    #a,b = results_to_csv(evaluate_on_all(original,lowercase_dataset=True),printRes=False,returnRes=True)
    #export_to_csv(txtResults=a, txtCov = b, name=name+'_SVD_'+str(n), filenameResults = 'dim_red', filenameCoverage = 'dim_redCoverage.csv')

    
    #del original
    
    
    #e_ppa = load_embedding(path+'_PPA_'+str(n), vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=n)
    #e_pca = load_embedding(path+'_PCA_'+str(n), vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=n)
    #e_svd = load_embedding(path+'_SVD_'+str(n), vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=n)

    #a,b = results_to_csv(evaluate_on_all(e_ppa,lowercase_dataset=True),printRes=False,returnRes=True)
    #export_to_csv(txtResults=a, txtCov = b, name=name+'_PPA_'+str(n), filenameResults = 'dim_red', filenameCoverage = 'dim_redCoverage.csv')
    
    #a,b = results_to_csv(evaluate_on_all(e_pca,lowercase_dataset=True),printRes=False,returnRes=True)
    #export_to_csv(txtResults=a, txtCov = b, name=name+'_PCA_'+str(n), filenameResults = 'dim_red', filenameCoverage = 'dim_redCoverage.csv')

    #a,b = results_to_csv(evaluate_on_all(e_svd,lowercase_dataset=True),printRes=False,returnRes=True)
    #export_to_csv(txtResults=a, txtCov = b, name=name+'_SVD_'+str(n), filenameResults = 'dim_red', filenameCoverage = 'dim_redCoverage.csv')

    return True

def add__reduction():
    #GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    
    test_reduction([GLOVE,jointcHYB],'GLOVE + jointcHYB')
    del GLOVE
    
    FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_reduction([FT,jointcHYB],'FT + jointcHYB')
    del FT
    
    LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_reduction([LEXVEC,jointcHYB],'LEXVEC + jointcHYB')
    del LEXVEC
    
    
    W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
    test_reduction([W2V,jointcHYB],'W2V + jointcHYB')
    del jointcHYB
    del W2V
    
    return True
    
    

def test_dim_reduction():
    #GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
    #W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
    #FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    #jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    #UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    #LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    #SKE = load_embedding(SketchEngine_web_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)
    #PDC = load_embedding(PDC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    
    
    #test_reduction([GLOVE,jointcHYB],'GLOVE + jointcHYB')
    GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_reduction([GLOVE,jointcHYB],'GLOVE + jointcHYB')
    if 'GLOVE' in locals():
        del GLOVE
    if 'jointcHYB' in locals():
        del jointcHYB
 
    FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_reduction([FT,jointcHYB],'FT + jointcHYB')
    
    if 'FT' in locals():
        del FT
    if 'jointcHYB' in locals():
        del jointcHYB
    
    W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_reduction([W2V,jointcHYB],'W2V + jointcHYB')
    if 'W2V' in locals():
        del W2V
    if 'jointcHYB' in locals():
        del jointcHYB
    
    LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_reduction([LEXVEC,jointcHYB],'LEXVEC + jointcHYB')
    
    if 'LEXVEC' in locals():
        del LEXVEC
    if 'jointcHYB' in locals():
        del jointcHYB
    
    FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_reduction([LEXVEC,jointcHYB,FT],'LEXVEC + jointcHYB + FT')

    if 'FT' in locals():
        del FT 
    if 'LEXVEC' in locals():
        del LEXVEC
    if 'jointcHYB' in locals():
        del jointcHYB
    
    FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_reduction([LEXVEC,jointcHYB,FT,UKB],'LEXVEC + jointcHYB + FT + UKB')
    
    
    '''
    UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
   
    test_reduction([FT,UKB],'FT + UKB')

    del UKB
    del FT
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
   
    test_reduction([jointcHYB,LEXVEC],'LEXVEC + jointcHYB')
   
    del jointcHYB
    del LEXVEC
    
    
    GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
    W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
    FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    SKE = load_embedding(SketchEngine_web_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)
    PDC = load_embedding(PDC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    
    
    test_reduction([GLOVE,W2V,jointcHYB],'GLOVE + W2V + jointcHYB',600)
    test_reduction([GLOVE,FT,jointcHYB],'GLOVE + FT + jointcHYB',600)
    test_reduction([GLOVE,W2V,jointcHYB],'GLOVE + W2V + jointcHYB',300)
    test_reduction([GLOVE,FT,jointcHYB],'GLOVE + FT + jointcHYB',300)
    
    test_reduction([W2V,FT,jointcHYB],'W2V + FT + jointcHYB',600)
    test_reduction([W2V,FT,jointcHYB],'W2V + FT + jointcHYB',300)
    
    test_reduction([LEXVEC,FT,jointcHYB,UKB],'LEXVEC + FT + jointcHYB + UKB',600)
    test_reduction([LEXVEC,FT,jointcHYB,UKB],'LEXVEC + FT + jointcHYB + UKB',300)
    
    test_reduction([LEXVEC,FT,W2V,GLOVE],'LEXVEC + FT + W2V + GLOVE',600)
    test_reduction([LEXVEC,FT,W2V,GLOVE],'LEXVEC + FT + W2V + GLOVE',300)
    
    test_reduction([LEXVEC,FT,W2V,jointcHYB],'LEXVEC + FT + W2V + jointcHYB',600)
    test_reduction([LEXVEC,FT,W2V,jointcHYB],'LEXVEC + FT + W2V + jointcHYB',300)
    
    test_reduction([GLOVE,W2V,FT,jointcHYB,UKB,LEXVEC,SKE,PDC],'GLOVE + W2V + FT + jointcHYB + UKB + LEXVEC + SKE + PDC',300)
    test_reduction([GLOVE,W2V,FT,jointcHYB,UKB,LEXVEC,SKE,PDC],'GLOVE + W2V + FT + jointcHYB + UKB + LEXVEC + SKE + PDC',900)
    test_reduction([GLOVE,W2V,FT,jointcHYB,UKB,LEXVEC,SKE,PDC],'GLOVE + W2V + FT + jointcHYB + UKB + LEXVEC + SKE + PDC',1200)
    
    '''
    
    return True





def sizeof_fmt(num, suffix='B'):
    ''' By Fred Cirera, after https://stackoverflow.com/a/1094933/1870254'''
    for unit in ['','Ki','Mi','Gi','Ti','Pi','Ei','Zi']:
        if abs(num) < 1024.0:
            return "%3.1f%s%s" % (num, unit, suffix)
        num /= 1024.0
    return "%.1f%s%s" % (num, 'Yi', suffix)



def print_memory_usage():
    print('>>> Virtual_memory (used): ' + str(psutil.virtual_memory().used / (1024.0 ** 3)) + ' GB')
    print('>>> Swap_memory (used): ' + str(psutil.swap_memory().used / (1024.0 ** 3)) + ' GB')
    print(' ')
    print(' ')  
    return True

def test_1_reduction(path,nameE):
    abs_path = os.path.join(path, nameE)
    with open(abs_path) as f:
        first_line = f.readline()
        first_line = first_line.split(' ')
        d = int(first_line[1])

    
    
    
    print(str(datetime.datetime.now()) + " Starting test algo, embedding: " + str(nameE))
    print_memory_usage()
    for name, size in sorted(((name, sys.getsizeof(value)) for name,value in locals().items()),
                             key= lambda x: -x[1])[:10]:
        print("{:>30}: {:>8}".format(name,sizeof_fmt(size)))
    e = load_embedding(abs_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=d)
    
    print(str(datetime.datetime.now()) + " Starting algo, embedding: " + str(nameE))
    print_memory_usage()
    for name, size in sorted(((name, sys.getsizeof(value)) for name,value in locals().items()),
                             key= lambda x: -x[1])[:10]:
        print("{:>30}: {:>8}".format(name,sizeof_fmt(size)))
    e.vectors = algo(e.vectors,300)
    print(str(datetime.datetime.now()) + " algo finished, embedding: " + str(nameE))
    print_memory_usage()
    for name, size in sorted(((name, sys.getsizeof(value)) for name,value in locals().items()),
                             key= lambda x: -x[1])[:10]:
        print("{:>30}: {:>8}".format(name,sizeof_fmt(size)))
    a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=str(nameE)+'_PPA_', filenameResults = 'dim_red_noL2.csv', filenameCoverage = 'dim_noL2_redCoverage.csv')
    
    del e
    del a
    del b
    
    print(str(datetime.datetime.now()) + " Starting test PCA, embedding: " + str(nameE))
    print_memory_usage()
    for name, size in sorted(((name, sys.getsizeof(value)) for name,value in locals().items()),
                             key= lambda x: -x[1])[:10]:
        print("{:>30}: {:>8}".format(name,sizeof_fmt(size)))
    e = load_embedding(abs_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=d)   
    print(str(datetime.datetime.now()) + " Starting PCA, embedding: " + str(nameE))
    print_memory_usage()
    for name, size in sorted(((name, sys.getsizeof(value)) for name,value in locals().items()),
                             key= lambda x: -x[1])[:10]:
        print("{:>30}: {:>8}".format(name,sizeof_fmt(size)))
    e.vectors = PCA(e.vectors,300)
    print(str(datetime.datetime.now()) + " PCA finished, embedding: " + str(nameE))
    print_memory_usage()
    for name, size in sorted(((name, sys.getsizeof(value)) for name,value in locals().items()),
                             key= lambda x: -x[1])[:10]:
        print("{:>30}: {:>8}".format(name,sizeof_fmt(size)))
    a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=str(nameE)+'_PCA_', filenameResults = 'dim_red_noL2.csv', filenameCoverage = 'dim_noL2_redCoverage.csv')
    
    del e
    del a
    del b
    
    print(str(datetime.datetime.now()) + " Starting test tSVD, embedding: " + str(nameE))
    print_memory_usage()
    for name, size in sorted(((name, sys.getsizeof(value)) for name,value in locals().items()),
                             key= lambda x: -x[1])[:10]:
        print("{:>30}: {:>8}".format(name,sizeof_fmt(size)))
    e = load_embedding(abs_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=d)   
    
    print(str(datetime.datetime.now()) + " Starting tSVD, embedding: " + str(nameE))
    print_memory_usage()
    for name, size in sorted(((name, sys.getsizeof(value)) for name,value in locals().items()),
                             key= lambda x: -x[1])[:10]:
        print("{:>30}: {:>8}".format(name,sizeof_fmt(size)))
    e.vectors = T_SVD(e.vectors,300)
    print(str(datetime.datetime.now()) + " tSVD finished, embedding: " + str(nameE))
    print_memory_usage()
    for name, size in sorted(((name, sys.getsizeof(value)) for name,value in locals().items()),
                             key= lambda x: -x[1])[:10]:
        print("{:>30}: {:>8}".format(name,sizeof_fmt(size)))
    a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=str(nameE)+'_tSVD_', filenameResults = 'dim_red_noL2.csv', filenameCoverage = 'dim_noL2_redCoverage.csv')
    
    del e
    del a
    del b
    
          
    print(str(datetime.datetime.now()) + " DONE, embedding: " + str(nameE))
    return True
    
   
    
    
def test_reduction2(path):
    dataset_min = get_vocab_simil_all(True)
    directory = os.fsencode(path)
    
   
    for filename in os.listdir(directory):
        test_1_reduction(directory,filename)
        
        

def test_retro(path):
    dataset_min = get_vocab_simil_all(True)
    directory = os.fsencode(path)
    for filename in os.listdir(directory):
        e = load_embedding(os.path.join(directory, filename), vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True)
        a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
        export_to_csv(txtResults=a, txtCov = b, name=str(filename)[2:-1], filenameResults = 'retro.csv', filenameCoverage = 'retroCoverage.csv')

        
        
def test_vecmap(embs,names,filename,normalize_embs):
    name = ''
    for n in range(len(names)):
        if n == len(names)-1:
             name = name+','+str(names[n])
        else:
            if n==0:
                name = str(names[n])
            else:
                name = name+'+'+str(names[n])
    
    c = avg_embeddings(embs, path='/home/concat.vec', vocabulary = dataset_min, weights=None, method="generate",generate_method='cosine',k=10,normalize=normalize_embs,where="return")
    a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=name, filenameResults = str(filename)+'.csv', filenameCoverage = str(filename)+'_coverage.csv')
    
    c = avg_embeddings(embs, path='/home/concat.vec', vocabulary = dataset_min, weights=None, method="ignore",generate_method='cosine',k=10,normalize=normalize_embs,where="return")
    a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=name, filenameResults = str(filename)+'_zeros.csv', filenameCoverage = str(filename)+'_zeros_coverage.csv')
    
    c = concatenate_embeddings(embs, path='/home/concat.vec', vocabulary = dataset_min, weights=None, method="generate",generate_method='cosine',k=10,normalize=normalize_embs,where="return")
    a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=name, filenameResults = str(filename)+'_concat.csv', filenameCoverage = str(filename)+'_concat.csv')
    
    return True

def test_vecmap_avg(embs,names,filename,normalize_embs):
    name = ''
    for n in range(len(names)):
        if n == len(names)-1:
             name = name+'+'+str(names[n])
        else:
            if n==0:
                name = str(names[n])
            else:
                name = name+'+'+str(names[n])
    
    c = avg_embeddings(embs, path='/home/concat.vec', vocabulary = dataset_min, weights=None, method="generate",generate_method='cosine',k=10,normalize=normalize_embs,where="return")
    a,b = results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=False,returnRes=True)
    export_to_csv(txtResults=a, txtCov = b, name=name, filenameResults = str(filename)+'_AVG.csv', filenameCoverage = str(filename)+'_AVG_coverage.csv')
    
    return True

def test_vecmap_FT_Orto():
    dataset_vocab = get_vocab_simil_all()
    dataset_min = get_vocab_simil_all(True)
    path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/FT(Orto)/'
    
    W2V = load_embedding(path+'W2V.FT-W2V.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    GLOVE = load_embedding(path+'GLOVE.FT-GLOVEL2.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    FT = load_embedding(path+'FT.FT-UKB.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(path+'Jointc.FT-Jointc.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    LEXVEC = load_embedding(path+'LEXVEC.FT-LEXVEC.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    UKB = load_embedding(path+'UKB.FT-UKB.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
  
    
    embs = [GLOVE,W2V,FT,jointcHYB,UKB,LEXVEC]
    names = ['GLOVE','W2V','FT','jointcHYB','UKB','LEXVEC']
    
    #De dos en dos
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            
            test_vecmap([embs[x],embs[y]],[names[x],names[y]],'toFT',False)
            test_vecmap([embs[x],embs[y]],[names[x],names[y]],'toFT_norm',True)
            
    #De tres en 3
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                test_vecmap([embs[x],embs[y],embs[j]],[names[x],names[y],names[j]],'toFT',False)
                test_vecmap([embs[x],embs[y],embs[j]],[names[x],names[y],names[j]],'toFT_norm',True)
  
    #de 4 en 4
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                   
                    test_vecmap([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z]],'toFT',False)
                    test_vecmap([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z]],'toFT_norm',True)
                   
    #de 5 en 5
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                       
                        test_vecmap([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v]],'toFT',False)
                        test_vecmap([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v]],'toFT_norm',True)
                          
                    
    #de 6 en 6
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                        for i in range(v+1,len(names)): 
                            
                            test_vecmap([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i]],'toFT',False)
                            test_vecmap([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i]],'toFT_norm',True)
                            
    return True


def test_vecmap_jointcHYB_Orto():
    dataset_vocab = get_vocab_simil_all()
    dataset_min = get_vocab_simil_all(True)
    path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/joint(Orto)/'
    
    W2V = load_embedding(path+'W2V.Jointc-W2V.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    GLOVE = load_embedding(path+'GLOVE.Jointc-GLOVEL2.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    FT = load_embedding(path+'FT.Jointc-FT.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(path+'Jointc.Jointc-UKB.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    LEXVEC = load_embedding(path+'LEXVEC.Jointc-LEXVEC.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    UKB = load_embedding(path+'UKB.Jointc-UKB.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
  
    
    embs = [GLOVE,W2V,FT,jointcHYB,UKB,LEXVEC]
    names = ['GLOVE','W2V','FT','jointcHYB','UKB','LEXVEC']
    
    #De dos en dos
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            
            test_vecmap([embs[x],embs[y]],[names[x],names[y]],'toJointc',False)
            test_vecmap([embs[x],embs[y]],[names[x],names[y]],'toJointc_norm',True)
            
    #De tres en 3
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                test_vecmap([embs[x],embs[y],embs[j]],[names[x],names[y],names[j]],'toJointc',False)
                test_vecmap([embs[x],embs[y],embs[j]],[names[x],names[y],names[j]],'toJointc_norm',True)
  
    #de 4 en 4
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                   
                    test_vecmap([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z]],'toJointc',False)
                    test_vecmap([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z]],'toJointc_norm',True)
                   
    #de 5 en 5
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                       
                        test_vecmap([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v]],'toJointc',False)
                        test_vecmap([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v]],'toJointc_norm',True)
                          
                    
    #de 6 en 6
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                        for i in range(v+1,len(names)): 
                            
                            test_vecmap([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i]],'toJointc',False)
                            test_vecmap([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i]],'toJointc_norm',True)
                            
    return True



def test_avg_normalized():
    dataset_vocab = get_vocab_simil_all()
    dataset_min = get_vocab_simil_all(True)
    path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/Normalized/'
    
    W2V = load_embedding(path+'W2V.NORMALIZED.Vecmap.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    GLOVE = load_embedding(path+'GLOVE.NORMALIZED.Vecmap.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    FT = load_embedding(path+'FT.NORMALIZED.Vecmap.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    jointcHYB = load_embedding(path+'JOINTC-HYB-ENES.NORMALIZED.Vecmap.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    LEXVEC = load_embedding(path+'LEXVEC.NORMALIZED.Vecmap.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    UKB = load_embedding(path+'UKB.NORMALIZED.Vecmap.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
  
    
    embs = [GLOVE,W2V,FT,jointcHYB,UKB,LEXVEC]
    names = ['GLOVE','W2V','FT','jointcHYB','UKB','LEXVEC']
    
    #De dos en dos
    for x in range(len(names)):
        for y in range(x+1,len(names)):
           
            test_vecmap_avg([embs[x],embs[y]],[names[x],names[y]],'toFT',False)
            
    #De tres en 3
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                test_vecmap_avg([embs[x],embs[y],embs[j]],[names[x],names[y],names[j]],'toFT',False)
                
  
    #de 4 en 4
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                   
                    test_vecmap_avg([embs[x],embs[y],embs[j],embs[z]],[names[x],names[y],names[j],names[z]],'toFT',False)
                    
                   
    #de 5 en 5
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                       
                        test_vecmap_avg([embs[x],embs[y],embs[j],embs[z],embs[v]],[names[x],names[y],names[j],names[z],names[v]],'toFT',False)
                        
                    
    #de 6 en 6
    for x in range(len(names)):
        for y in range(x+1,len(names)):
            for j in range(y+1,len(names)): 
                for z in range(j+1,len(names)): 
                    for v in range(z+1,len(names)): 
                        for i in range(v+1,len(names)): 
                            
                            test_vecmap_avg([embs[x],embs[y],embs[j],embs[z],embs[v],embs[i]],[names[x],names[y],names[j],names[z],names[v],names[i]],'toFT',False)
                           
                            
    return True


def test_vecmap_FT():
    path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/FT/'
    
    a = load_embedding(path+'1_FT.FT-Jointc.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'1_Jointc.FT-Jointc.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['FT,JointcHYB'],'WtoFT',False)
    test_vecmap([a,b],['FT,JointcHYB'],'WtoFT_norm',True)  
    
    a = load_embedding(path+'2_FT.FT-LEXVEC.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'2_LEXVEC.FT-LEXVEC.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['FT,LEXVEC'],'WtoFT',False)
    test_vecmap([a,b],['FT,LEXVEC'],'WtoFT_norm',True)  
    
    a = load_embedding(path+'3_FT.FT-UKB.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'3_UKB.FT-UKB.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['FT,UKB'],'WtoFT',False)
    test_vecmap([a,b],['FT,UKB'],'WtoFT_norm',True) 
    
    a = load_embedding(path+'4_FT.FT-W2V.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'4_W2V.FT-W2V.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['FT,W2V'],'WtoFT',False)
    test_vecmap([a,b],['FT,W2V'],'WtoFT_norm',True)
    
    a = load_embedding(path+'5_FT.W2V-GLOVEL2.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'5_GLOVE.FT-GLOVEL2.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['FT,GLOVE'],'WtoFT',False)
    test_vecmap([a,b],['FT,GLOVE'],'WtoFT_norm',True) 
    

def test_vecmap_jointcHYB():
    path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/joint/'
    
    a = load_embedding(path+'1_FT.Jointc-FT.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'1_Jointc.Jointc-FT.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['FT,JointcHYB'],'WtoJointc',False)
    test_vecmap([a,b],['FT,JointcHYB'],'WtoJointc_norm',True)  
    
    a = load_embedding(path+'3_GLOVE.Jointc-GLOVEL2.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'3_Jointc.Jointc-GLOVEL2.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['Jointc,GLOVE'],'WtoJointc',False)
    test_vecmap([a,b],['Jointc,GLOVE'],'WtoJointc_norm',True)  
    
    a = load_embedding(path+'4_Jointc.Jointc-UKB.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'4_Jointc.Jointc-UKB.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['Jointc,UKB'],'WtoJointc',False)
    test_vecmap([a,b],['Jointc,UKB'],'WtoJointc_norm',True) 
    
    a = load_embedding(path+'5_Jointc.Jointc-LEXVEC.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'5_LEXVEC.Jointc-LEXVEC.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['Jointc,LEXVEC'],'WJointc',False)
    test_vecmap([a,b],['Jointc,LEXVEC'],'WJointc_norm',True)
    
    a = load_embedding(path+'6_Jointc.Jointc-W2V.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    b = load_embedding(path+'6_W2V.Jointc-W2V.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    test_vecmap([a,b],['Jointc,W2V'],'WJointc',False)
    test_vecmap([a,b],['Jointc,W2V'],'WJointc_norm',True) 

In [13]:
#DIM_REDUCTION.py
#https://arxiv.org/pdf/1708.03629.pdf
#https://github.com/vyraun/Half-Size/blob/master/pca_ppa.py
#from skcuda.linalg import PCA as cuPCA
import numpy as np
from sklearn import decomposition
#import pycuda.autoinit
#import pycuda.gpuarray as gpuarray
import numpy as np
#import skcuda.linalg as linalg
from sklearn.preprocessing import StandardScaler

def PPA(matrix):
    # PCA to get Top Components
    n = matrix.shape[1]
    pca =  decomposition.PCA(n_components = n)
    X_train = matrix - np.mean(matrix)
    X_fit = pca.fit_transform(X_train)
    U1 = pca.components_
    
    z = []
    
    # Removing Projections on Top Components
    for i, x in enumerate(X_train):
        for u in U1[0:7]:        
            x = x - np.dot(u.transpose(),x) * u 
        z.append(x)

    return np.asarray(z)

def PCA(matrix, n):
    pca = decomposition.PCA(n_components = n)
    #SKLEARN CENTERS DE DATA, THIS IS REDUNTDANT. 
    X_train = matrix - np.mean(matrix)
    return pca.fit_transform(X_train)


def algo(matrix, n_components):
    #matrixPPA= PPA(matrix)
    #matrixR = PCA(matrixPPA,n_components)
    #print(matrixR.shape)
    #del matrixPPA
    #return PPA(matrixR)
    return PPA(PCA(PPA(matrix),n_components))

def T_SVD(matrix,n):
    svd = decomposition.TruncatedSVD(n_components = n)
    return svd.fit_transform(matrix)


def PPA_cuda(matrix):
    # PCA to get Top Components
    n = matrix.shape[1]
    pca =  linalg.PCA(n_components = n)
    X_train = matrix - np.mean(matrix)
    X_fit = pca.fit_transform(X_train)
    U1 = pca.components_
    
    z = []
    
    # Removing Projections on Top Components
    for i, x in enumerate(X_train):
        for u in U1[0:7]:        
            x = x - np.dot(u.transpose(),x) * u 
        z.append(x)

    return np.asarray(z)

def PCA_cuda(matrix, n):
    #matrix = StandardScaler().fit_transform(matrix)
    pca = cuPCA(n_components = n)
    X_gpu = gpuarray.GPUArray((matrix.shape[0],matrix.shape[1]), type(matrix[0][0]), order="F") 
    X_gpu.set(matrix)
    return pca.fit_transform(X_gpu).get()





## Embeddings

In [14]:

W2V_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/GoogleNews-vectors-negative300.bin'
GLOVE_CC_42_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/Glove/glove.42B.300d.txt'
GLOVE_CC_840_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/Glove/glove.840B.300d.txt'
GLOVE_WIKI_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/Glove/glove.6B.300d.txt'
FastText_WIKI_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/fastTextPretrained/2017/wiki-news-300d-1M.vec'
FastText_CC_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/fastTextPretrained/2017/crawl-300d-2M.vec'
UKB_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/UKB/RWSGwn.emb'
SketchEngine_BritishNational_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/fastTextPretrained/bnc2_tt2.vec'
SketchEngine_web_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/fastTextPretrained/ententen13_tt2_1.vec'
Numberbatch_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/Conceptnet/numberbatch-en.txt'
NAACL_DeepWalk_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/NAACL/DT_embeddings_DeepWalk'
NAACL_Line_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/NAACL/DT_embeddings_LINE'
NAACL_Node2Vec_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/NAACL/DT_embeddings_Node2vec'
NAACL_Nodes_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/NAACL/DT_nodes'
Turian_100_path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/Turian/hlbl_reps_clean_1.rcv1.clean.tokenized-CoNLL03.case-intact.txt'

Senna_words_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/Senna/words.lst'
Senna_vectors_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/Senna/embeddings.txt'
Multilingual512_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/FaruquiAndDyer multilingual 512/vec.txt'
SW2_cbow_wikipedia = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/SW2V/sw2v_cbow_wikipedia_vectors.bin'
SW2_synsets_cbow_wikipedia = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/SW2V/sw2v_synsets_cbow_wikipedia_vectors.bin'
mscc_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/contex2vec/mscc.skipgram.w10.d600.neg10.iter5.words'
ukwac_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/contex2vec/ukwac.skipgram.w10.d600.neg10.iter3.words'
jointcHYB_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/jointcHYB/JOINTC-HYB-ENES.emb'
lexvec = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/lexvec/lexvec.ngramsubwords.300d.W.pos.vectors/data'
PDC_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/PDC && HDC/wikicorp.201004-pdc-iter-20-alpha-0.05-window-10-dim-300-neg-10-subsample-0.0001.txt'
HDC = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/PDC && HDC/wikicorp.201004-hdc-iter-20-alpha-0.025-window-10-dim-300-neg-10-subsample-0.0001.txt'

FT_FT_UKB_ORTO_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/FT.FT-UKB.Orto.TXT'
UKB_FT_UKB_ORTO_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/UKB.FT-UKB.Orto.TXT'
FT_UKB_FT_ORTO_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/FT.FT-UKB.Orto.TXT'
UKB_UKB_FT_ORTO_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/UKB.FT-UKB.Orto.TXT'
W2V_FT_W2V_ORTO_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/W2V.FT-W2V.Orto.TXT'
GLOVE_FT_GLOVE_ORTO_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/GLOVE.FT-GLOVE.Orto.TXT'
W2V_GLOVE_W2V_ORTO_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/W2V.GLOVE-W2V.Orto.TXT'
GLOVE_GLOVE_W2V_ORTO_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/GLOVE.GLOVE-W2V.Orto.TXT'


FT_UKB_FT_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/FT.FT-UKB.TXT'
UKB_UKB_FT_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/UKB.FT-UKB.TXT'
FT_FT_UKB_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/FT.FT-UKB.TXT'
UKB_FT_UKB_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapRemap/UKB.FT-UKB.TXT'

MEAN_FT_UKB_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapCombinations/FT.UKB.recommended.original'
MEAN_FT_UKB_ORTO_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapCombinations/FT.UKB.recommended.Orto'

MEAN_FT_W2VGLOVE_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapCombinations/FT_GLOVE.W2V.recommended.Orto'
MEAN_GLOVE_W2VGLOVE_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/VecmapCombinations/GLOVE_GLOVE.W2V.recommended.Orto'

FT_Vecmap_Normalized_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/Normalized/FT.NORMALIZED.Vecmap.TXT'
UKB_Vecmap_Normalized_path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1//TFG/vecmap_results/Normalized/UKB.NORMALIZED.Vecmap.TXT'





In [15]:
dataset_vocab = get_vocab_simil_all()
dataset_min = get_vocab_simil_all(True)

In [ ]:
results_to_csv(evaluate_on_all_avg([FT,UKB,LEXVEC,jointcHYB],lowercase_dataset=True))

In [ ]:
GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)

In [ ]:
GLOVE = load_embedding(GLOVE_WIKI_path, vocabulary = None, length_normalize = True, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)

In [ ]:
GLOVE = load_embedding(GLOVE_CC_42_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)

In [ ]:
W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)

In [ ]:
FT = load_embedding(FastText_WIKI_path, vocabulary = dataset_vocab, length_normalize = True, normalize_dimensionwise=False, dims_restriction=300)

In [ ]:
FT = load_embedding(FastText_CC_path, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
jointcHYB = load_embedding(jointcHYB_path, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
UKB = load_embedding(UKB_path, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
del UKB

In [ ]:
LEXVEC = load_embedding(lexvec, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
SKE = load_embedding(SketchEngine_BritishNational_path, vocabulary = dataset_vocab, length_normalize = True, normalize_dimensionwise=False, delete_duplicates=False)

In [ ]:
SKE = load_embedding(SketchEngine_web_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)

In [ ]:
Numberbatch = load_embedding(Numberbatch_path, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False)

In [ ]:
PDC = load_embedding(PDC, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
NAACL = load_embedding(NAACL_DeepWalk_path, vocabulary = None, length_normalize = True)

In [ ]:
Turian = load_embedding(Turian_100_path)

In [ ]:
senna = load_embedding(Senna_words_path, path2=Senna_vectors_path, format = "senna")

In [ ]:
FT_UKB_FT = load_embedding(FT_UKB_FT_path, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
UKB_UKB_FT = load_embedding(UKB_UKB_FT_path, length_normalize = True, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)

In [ ]:
FT_FT_UKB = load_embedding(FT_FT_UKB_path, vocabulary = dataset_vocab, length_normalize = True, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)

In [ ]:
FT_FT_UKB_ORTO = load_embedding(FT_FT_UKB_ORTO_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
UKB_FT_UKB_ORTO = load_embedding(UKB_FT_UKB_ORTO_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
FT_Vecmap_Normalized = load_embedding(FT_Vecmap_Normalized_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
UKB_Vecmap_Normalized = load_embedding(UKB_Vecmap_Normalized_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)


In [ ]:
UKB_FT_UKB = load_embedding(UKB_FT_UKB_path, vocabulary = dataset_vocab, length_normalize = True, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)

In [ ]:
MEAN_FT_UKB = load_embedding(MEAN_FT_UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300) 

In [ ]:
MEAN_FT_UKB_ORTO = load_embedding(MEAN_FT_UKB_ORTO_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300) 

In [ ]:
W2V_FT_W2V_ORTO = load_embedding(W2V_FT_W2V_ORTO_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
GLOVE_FT_GLOVE_ORTO = load_embedding(GLOVE_FT_GLOVE_ORTO_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
W2V_GLOVE_W2V_ORTO = load_embedding(W2V_GLOVE_W2V_ORTO_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
GLOVE_GLOVE_W2V_ORTO = load_embedding(GLOVE_GLOVE_W2V_ORTO_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
MEAN_FT_W2VGLOVE = load_embedding(MEAN_GLOVE_W2VGLOVE_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
MEAN_GLOVE_W2VGLOVE = load_embedding(MEAN_GLOVE_W2VGLOVE_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
#E = load_embedding(UKB_path, lower =False, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False)
#E.length_normalize()
#(results_to_csv(evaluate_on_all(E,lowercase_dataset=True),printRes=True,returnRes=True),'UKB')
a,b = results_to_csv(evaluate_on_all(E,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='UKB')

In [ ]:
v = set(standarize_words(N1.words,unicode=False, lower=True))

In [ ]:
N1 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/FTL1rm.Jointc-FTr.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
N2 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/UKBrm.Jointc-UKBr.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#N3 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/Jointc.Jointc-LEXVEC.Orto.TXT', vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#N4 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/LEXVEC.Jointc-LEXVEC.Orto.TXT', vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#N5 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/NUMBERBATCH_N.Jointc-NUMBERBATCH.Orto.TXT', vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#N6 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/Normalized/JOINTC-HYB-ENES-retro.NORMALIZED.Vecmap.TXT', vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#N7 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/jointcHYB_retro_ppdb.txt', vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

#N8 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/FTL1rm.Jointc-FTr.Orto.TXT', vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#N9 = 
#N10 =


#N1.mean_center()
#N2.mean_center()
#N3.mean_center()
#N4.mean_center()
#N5.mean_center()


#from sklearn.preprocessing import StandardScaler
#scaler = StandardScaler()
#scaler.fit(N1.vectors)
#scaler.fit(N1.vectors)
#scaler.fit(N1.vectors)
#scaler.fit(N1.vectors)
#N2.vectors = scaler.transform(N2.vectors)


In [ ]:

a = avg_embeddings([N1,N2], path ='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/FTrm+UKBrm_genC.vec' ,vocabulary = None, method = "ignore",generate_method='cosine', where="return")

#N = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/FTrm+UKBrm_genC.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)


#N.L1_dimensionwwise()
results_to_csv(evaluate_on_all(a, lowercase_dataset=True))

In [ ]:
a = avg_embeddings_generate_multithread([N1,N2], path ='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/FTrm+UKBrm_genC', vocabulary = None, weights=None, method = "generate",generate_method='cosine',k=10)


In [ ]:
list_embsE1 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/UKB_retro_ppdb.txt', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#E1.L1_dimensionwwise()
E2 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/ft_retro_ppdb.txt', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#E2.L1_dimensionwwise()

In [ ]:
results_to_csv(evaluate_on_all_avg([E1,E2], lowercase_dataset=True))

In [ ]:
E1.export('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/UKB_retro_ppdb.txt')
E2.export('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/ft_retro_ppdb.txt')

In [ ]:
GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
W2V = load_embedding(W2V_path, vocabulary = dataset_vocab, format='bin', length_normalize = False, normalize_dimensionwise=False)
FT = load_embedding(FastText_CC_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
jointcHYB = load_embedding(jointcHYB, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
UKB = load_embedding(UKB_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
LEXVEC = load_embedding(lexvec, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
SKE = load_embedding(SketchEngine_web_path, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)
PDC = load_embedding(PDC, vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
results_to_csv(evaluate_on_all_avg([GLOVE],[1]))

In [ ]:
embs = [FT, jointcHYB, UKB, LEXVEC,GLOVE,W2V,SKE,PDC]
weights = [8,7,6,5,4,3,2,1]

#A = avg_embeddings(embs, weights=weights, method = "ignore", where="return")
C = concatenate_embeddings(embs, method="zeros",where="return")
print("AVG")
#results_to_csv(evaluate_on_all(A))
print("CONCAT")
results_to_csv(evaluate_on_all(C))

In [ ]:
del GLOVE

In [ ]:
GLOVE = load_embedding('/media/iker/My Book/TFG/Glove/GLOVE.CC.L2Normalized.WHEADER.vec', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
del A
del C

In [ ]:
GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
GLOVE.export('/media/iker/My Book/TFG/Emb_preprocesing/GLOVE.vec',False)
del GLOVE
W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
W2V.export('/media/iker/My Book/TFG/Emb_preprocesing/W2V.vec',False)
del W2V
FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
FT.export('/media/iker/My Book/TFG/Emb_preprocesing/FT.vec',False)
del FT
jointcHYB = load_embedding(jointcHYB, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
jointcHYB.export('/media/iker/My Book/TFG/Emb_preprocesing/jointcHYB.vec',False)
del jointcHYB
UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
UKB.export('/media/iker/My Book/TFG/Emb_preprocesing/UKB.vec',False)
del UKB
LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
LEXVEC.export('/media/iker/My Book/TFG/Emb_preprocesing/LEXVEC.vec',False)
del LEXVEC
SKE = load_embedding(SketchEngine_web_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)
SKE.export('/media/iker/My Book/TFG/Emb_preprocesing/SKE.vec',False)
del SKE
PDC = load_embedding(PDC, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
PDC.export('/media/iker/My Book/TFG/Emb_preprocesing/PDC.vec',False)
del PDC

In [ ]:
concatenate_embeddings(embs, path='/home/concat.vec', vocabulary = None, method="zeros",where="file"):

In [ ]:
#FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#joint = load_embedding(jointcHYB, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#concatenate_embeddings([FT,joint], path='/media/iker/My Book/TFG/Concatenated/FT+joint.vec', vocabulary = None, method="zeros",where="file")
#del joint
#
#UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#concatenate_embeddings([FT,UKB], path='/media/iker/My Book/TFG/Concatenated/FT+UKB.vec', vocabulary = None, method="zeros",where="file")
#del UKB

#LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#concatenate_embeddings([FT,LEXVEC], path='/media/iker/My Book/TFG/Concatenated/FT+LEXVEC.vec', vocabulary = None, method="zeros",where="file")
#del LEXVEC

#GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
#concatenate_embeddings([FT,GLOVE], path='/media/iker/My Book/TFG/Concatenated/FT+GLOVE.vec', vocabulary = None, method="zeros",where="file")

##REDUCIR
E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+joint.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = algo(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+joint_ALGO300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+joint.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = PCA(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+joint_PCA300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+joint.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = T_SVD(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+joint_SVD300.vec')
del E
###

E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+UKB.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = algo(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+UKB_algo300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+UKB.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = PCA(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+UKB_PCA300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+UKB.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = T_SVD(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+UKB_SVD300.vec')
del E
###


E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+LEXVEC.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = algo(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+LEXVEC_algo300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+LEXVEC.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = PCA(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+LEXVEC_PCA300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+LEXVEC.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = T_SVD(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+LEXVEC_SVD300.vec')
del E
###

E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+GLOVE.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = algo(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+GLOVE_algo300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+GLOVE.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = PCA(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+GLOVE_PCA300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/FT+GLOVE.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = T_SVD(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/FT+GLOVE_SVD300.vec')
del E
###





In [ ]:
W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
joint = load_embedding(jointcHYB, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
concatenate_embeddings([W2V,joint], path='/media/iker/My Book/TFG/Concatenated/W2V+joint.vec', vocabulary = None, method="zeros",where="file")
del W2V
del joint

E = load_embedding('/media/iker/My Book/TFG/Concatenated/W2V+joint.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = algo(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/W2V+joint_algo300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/W2V+joint.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = PCA(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/W2V+joint_PCA300.vec')
del E
E = load_embedding('/media/iker/My Book/TFG/Concatenated/W2V+joint.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=600)
E.vectors = T_SVD(E.vectors,300)
E.export('/media/iker/My Book/TFG/Concatenated/W2V+joint_SVD300.vec')
del E


In [ ]:
FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
generate_dictionary_for_vecmap(FT, LEXVEC, '/media/iker/My Book/TFG/vecmap_results/vocab/FT.LEXVEC.dic', return_dict = False)

del LEXVEC

PDC = load_embedding(PDC, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
generate_dictionary_for_vecmap(FT, PDC, '/media/iker/My Book/TFG/vecmap_results/vocab/FT.PDC.dic', return_dict = False)
del PDC

jointcHYB = load_embedding(jointcHYB, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
generate_dictionary_for_vecmap(FT, jointcHYB, '/media/iker/My Book/TFG/vecmap_results/vocab/FT.jointcHYB.dic', return_dict = False)
del jointcHYB


In [ ]:
jointcHYB = load_embedding(jointcHYB, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
generate_dictionary_for_vecmap(jointcHYB, FT, '/media/iker/My Book/TFG/vecmap_results/vocab/jointcHYB.FT.dic', return_dict = False)
del FT
GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
generate_dictionary_for_vecmap(jointcHYB, GLOVE, '/media/iker/My Book/TFG/vecmap_results/vocab/jointcHYB.GLOVE.dic', return_dict = False)
del GLOVE

UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
generate_dictionary_for_vecmap(jointcHYB, UKB, '/media/iker/My Book/TFG/vecmap_results/vocab/jointcHYB.UKB.dic', return_dict = False)
del UKB


W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
generate_dictionary_for_vecmap(jointcHYB, W2V, '/media/iker/My Book/TFG/vecmap_results/vocab/jointcHYB.W2V.dic', return_dict = False)
del W2V

LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
generate_dictionary_for_vecmap(jointcHYB, LEXVEC, '/media/iker/My Book/TFG/vecmap_results/vocab/jointcHYB.LEXVEC.dic', return_dict = False)
del LEXVEC


In [ ]:
N1 = load_embedding('/media/iker/My Book/TFG/vecmap_results/Normalized/UKB.NORMALIZED.Vecmap.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
N2 = load_embedding('/media/iker/My Book/TFG/vecmap_results/Normalized/FT.NORMALIZED.Vecmap.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#D1 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/Jointc.Jointc-FT.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#D2 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/FT.Jointc-FT.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#O1 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/Jointc.Jointc-FT.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#O2 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/FT.Jointc-FT.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
print("Result from vecmap 1:")
results_to_csv(evaluate_on_all(D1))
print(" ")

In [ ]:
    
print("Result from vecmap 2:")
results_to_csv(evaluate_on_all(D2))
print(" ")

In [ ]:
print("Normalization vecmap 1:")
results_to_csv(evaluate_on_all(N1))
print(" ")
    

In [ ]:
print("Normalization vecmap 2:")
results_to_csv(evaluate_on_all(N2))

In [ ]:
print("Similarity AVG D:")
results_to_csv(evaluate_on_all_avg([D1,D2]))

In [ ]:
print("Similarity AVG Orto:")
results_to_csv(evaluate_on_all_avg([N1,N2]))

In [ ]:
print("Average")
avg = avg_embeddings([N1,N2], method = "ignore", where="return")
results_to_csv(evaluate_on_all(avg))

In [ ]:
print("Concatenate")
concat = concatenate_embeddings([N1,N2], method = "skip", where="return")
results_to_csv(evaluate_on_all(concat))

In [ ]:
print("D Mean")
avg = avg_embeddings([D1,D2], method = "ignore", where="return")
results_to_csv(evaluate_on_all(avg))

In [ ]:
print("D Concat")
concat = concatenate_embeddings([D1,D2], method = "zeros", where="return")
results_to_csv(evaluate_on_all(concat))

In [ ]:
print("Orto Mean")
avg = avg_embeddings([O1,O2], method = "ignore", where="return")
results_to_csv(evaluate_on_all(avg))

In [ ]:
print("Orto Concat")

In [ ]:
concat = concatenate_embeddings([O1,O2], method = "zeros", where="return")
results_to_csv(evaluate_on_all(concat))

In [ ]:
#O1 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/Jointc.Jointc-FT.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
O2 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/FT.Jointc-FT.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#O3 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/LEXVEC.Jointc-LEXVEC.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
O4 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/UKB.Jointc-UKB.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
O5 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/Numberbatch.Jointc-Numberbatch.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
O6 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/NUMBERBATCH_N.Jointc-NUMBERBATCH.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
O5 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/W2V.Jointc-W2V.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
O6 = load_embedding('/media/iker/My Book/TFG/vecmap_results/vecmap-master/GLOVE.Jointc-GLOVEL2.Orto.TXT', vocabulary = dataset_vocab, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)


In [ ]:
avg = avg_embeddings([O2,O4,O6],weights=[1,1,2], method = "ignore", where="return")
#avg2 = avg_embeddings([O1,O2], method = "ignore", where="return")

#avg = avg_embeddings([avg,Numberbatch], method = "ignore", where="return")
#concat = concatenate_embeddings([avg,Numberbatch], method = "zeros", where="return")


results_to_csv(evaluate_on_all_avg([avg]))

In [ ]:
concat = concatenate_embeddings([O2,O4,O5], method = "zeros", where="return")
results_to_csv(evaluate_on_all(concat))

In [ ]:
concat = concatenate_embeddings([FT,UKB], method = "skip", where="return")
results_to_csv(evaluate_on_all(concat))

In [ ]:
dataset_vocab = get_vocab_simil_all(True)

In [ ]:

Retro = load_embedding('/media/iker/My Book/TFG/GoogleNews-vectors-negative300.txt', lower =True, vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=300)
(evaluate_on_all(Retro,lowercase_dataset=True))

In [ ]:
Retro.word_to_vector('cd',False)

In [ ]:
len(dataset_vocab)

In [ ]:
generate_dictionary_for_vecmap(FT, Numberbatch, '/media/iker/My Book/TFG/vecmap_results/vocab/FT.Numberbatch.dic', return_dict = False)


In [ ]:
jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
generate_dictionary_for_vecmap(jointcHYB, Numberbatch, '/media/iker/My Book/TFG/vecmap_results/vocab/jointcHYB.Numberbatch.dic', return_dict = False)
del jointcHYB

In [ ]:
test_normalization(W2V_path,embformat='bin', dims_restriction = 300, delete_duplicates = True, lowercase_datasets=False)

In [ ]:
test_normalization(UKB_path,embformat='text', dims_restriction = 300, delete_duplicates = True, lowercase_datasets=True)

In [ ]:
test_normalization(GLOVE_CC_840_path,embformat='text', dims_restriction = 300, delete_duplicates = True, lowercase_datasets=False)

In [ ]:
test_normalization(FastText_CC_path,embformat='text', dims_restriction = 300, delete_duplicates = True, lowercase_datasets=False)

In [ ]:
test_normalization(lexvec,embformat='text', dims_restriction = 300, delete_duplicates = True, lowercase_datasets=False)

In [ ]:
test_normalization(jointcHYB_path,embformat='text', dims_restriction = 300, delete_duplicates = True, lowercase_datasets=True)

In [ ]:
test_normalization(SketchEngine_web_path,embformat='text', dims_restriction = 100, delete_duplicates = True, lowercase_datasets=True)

In [ ]:
i=1
#del dX
dy = []
for name, data in iteritems(datasets):
    if i == 1:
        dX = data.X
        i=2
    else:
        dX=np.append(dX,data.X,axis=0)
    print(len(data.X))
    dy=np.append(dy,data.y)
    

In [ ]:
 for name, data in iteritems(datasets):
        d = {'dataset':name}
        d.update(similarity_emd(emb, data.X, data.y, backoff_embs,lowercase_dataset))
        

In [ ]:
dX.shape

In [ ]:
len(dy)

In [ ]:
embs = [
    ['hola','routube','type',400,'data'],
    ['hola2','routube2','type2',402,'data2']
    
    
]

In [ ]:
  embs = {
    'GLOVE' : [1,2],
    'PDC' : [2,3]
  }

In [ ]:
names =['a','b','c']

for x in range(len(names)):
        for y in range(x+1,len(names)):
            print(y)

In [ ]:
import itertools
list(itertools.permutations([1, 2, 3]))

In [ ]:
combinations([1,2,3])

In [ ]:
stuff = [1, 2, 3,4]
for L in range(1, len(stuff)+1):
    for subset in itertools.combinations(stuff, L):
        print(np.asarray(subset))

In [ ]:
for i in range(len(stuff)):
    li=[i]
    for j in range(i+1,len(stuff)):
        lo = np.append(li,j)
        for l in range(j+1,len(stuff)):
            la = np.append(lo,l)
            print(la)

In [ ]:
test_similarity_avg()

In [ ]:
'"'+str(np.array(subset))+'"'

In [ ]:
a = ["a","b","c"]
b = ["w","asda","a"]
c = ["a","b","c"]

w = [a,b,c]

In [ ]:
v = Vocabulary(["a","b","c","d","e","f","g","h","i","j","k","l","m","n","o","p","q"])
v2 = Vocabulary(["a","kase","c","d","e","f","g","h","i","j","k","l","m","n","o","p","q"])
#v3 = Vocabulary(["qsae","hola","q","ase"])

e1 = Embedding(v, [[1,2],[2,3],[3,4],[4,5],[5,6],[6,7],[7,8],[8,9],[9,10],[10,11],[11,12],[12,13],[13,14],[14,15],[15,16],[16,17],[17,18]])
e2 = Embedding(v2, [[1,2],[100,100],[3,4],[4,5],[5,6],[6,7],[7,8],[8,9],[9,10],[10,11],[11,12],[12,13],[13,14],[14,15],[15,16],[16,17],[17,18]])
#e3 = Embedding(v3, [1,2,3,4])


In [ ]:
generate_overlapping_vocab([e1])

In [ ]:
np.append([1,2,3],[3,4,5],axis=0)

In [ ]:
2.241242/len([1,2,3])

In [ ]:
generate_word(e1,[e1,e2],"kase",overlapping_vocab=None,number_of_words = 10)

In [ ]:

UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
#concatenate_embeddings([FT,UKB], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/FT+UKB_generated', vocabulary = dataset_min, method="generate",where="file")
avg_embeddings([FT,UKB], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/FT+UKB_generated', vocabulary = dataset_min, weights=None, method = "generate", where="file")

In [ ]:
del UKB
LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
concatenate_embeddings([FT,LEXVEC], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/FT+LEXVEC_generated', vocabulary = dataset_min, method="generate",where="file")
avg_embeddings([FT,LEXVEC], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/FT+LEXVEC_generated', vocabulary = dataset_min, weights=None, method = "generate", where="file")

In [ ]:
del LEXVEC
jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=300)



In [ ]:
concatenate_embeddings([FT,jointcHYB], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/FT+jointcHYB_generated', vocabulary = dataset_min, method="generate",where="file")
avg_embeddings([FT,jointcHYB], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/FT+jointcHYB_generated', vocabulary = dataset_min, weights=None, method = "generate", where="file")

In [ ]:
del jointcHYB
del FT

In [ ]:
UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)

In [ ]:
concatenate_embeddings([W2V,UKB], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/W2V+UKB_generated', vocabulary = dataset_min, method="generate",where="file")
avg_embeddings([W2V,UKB], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/W2V+UKB_generated', vocabulary = dataset_min, weights=None, method = "generate", where="file")

In [ ]:
del UKB
del W2V

In [ ]:
e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/FT+UKB_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=600)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='FT+UKB generated')


e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/FT+UKB_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=300)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='FTmUKB generated')



e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/FT+LEXVEC_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=600)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='FT+LEXVEC generated')


e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/FT+LEXVEC_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=300)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='FTuLEXVEC generated')


e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/FT+jointcHYB_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=600)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='FT+jointcHYB generated')

e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/FT+jointcHYB_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=300)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='FTujointcHYB generated')

e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/W2V+UKB_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=600)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='W2V+UKB generated')
              
e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/W2V+UKB_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=300)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='W2VuUKB generated')

In [ ]:
e.words

In [ ]:
del e
UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=300)


In [ ]:
concatenate_embeddings([FT,UKB,LEXVEC,jointcHYB], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/FT+UKB+LEXVEC+jointcHYB_generated', vocabulary = dataset_min, method="generate",where="file")
avg_embeddings(FT,UKB,LEXVEC,jointcHYB], path='/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/FT+UKB+LEXVEC+jointcHYB_generated', vocabulary = dataset_min, weights=None, method = "generate", where="file")

In [ ]:
del UKB
del FT
del LEXVEC
del jointcHYB

e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/FT+UKB+LEXVEC+jointcHYB_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=300)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='FT+UKB+LEXVEC+jointcHYB_generated'
              
e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Mean/FT+UKB+LEXVEC+jointcHYB_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=False, dims_restriction=300)
a,b = results_to_csv(evaluate_on_all(e,lowercase_dataset=True),printRes=False,returnRes=True)
export_to_csv(txtResults=a, txtCov = b, name='FTuUKBuLEXVECujointcHYB_generated'

In [ ]:
e = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/FT+UKB+LEXVEC+jointcHYB_generated', vocabulary = None, length_normalize = False, normalize_dimensionwise=False)


In [ ]:
a = set([1,2,3,4,45,6,1,2,3,3,3,3,3,3,3,3,88,1,2,11])

In [ ]:
for w in a:
    print(w)

In [ ]:
Retro = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/jointcHYB_retro_ppdb.txt', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
Retro.export('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra-2.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/jointcHYB_retro_ppdb.txt -o JOINTC-HYB-ENES-retro.NORMALIZED.Vecmap.TXT')

In [ ]:
FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
merge_vocab_generator(UKB,[FT],path='/home/iker/Escritorio/Meta/Res/UKBwFT',vocab=dataset_min, method = 'cosine', k = 10)
merge_vocab_generator(FT,[UKB],path='/home/iker/Escritorio/Meta/Res/FTwUKB',vocab=dataset_min, method = 'cosine', k = 10)


In [ ]:
FT = load_embedding('/home/iker/Escritorio/Meta/Res/FTwUKB.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
UKB = load_embedding('/home/iker/Escritorio/Meta/Res/UKBwFT.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

In [ ]:
results_to_csv(evaluate_on_all_avg([FT,UKB], lowercase_dataset=True))

In [ ]:
GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = True, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
W2V = load_embedding(W2V_path, vocabulary = dataset_min, format='bin', length_normalize = True, normalize_dimensionwise=False)
FT = load_embedding(FastText_CC_path, vocabulary = dataset_min, length_normalize = True, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
jointcHYB = load_embedding(jointcHYB_path, vocabulary = dataset_min, length_normalize = True, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
UKB = load_embedding(UKB_path, vocabulary = dataset_min, length_normalize = True, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
LEXVEC = load_embedding(lexvec, vocabulary = dataset_min, length_normalize = True, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
SKE = load_embedding(SketchEngine_web_path, vocabulary = dataset_min, length_normalize = True, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)
PDC = load_embedding(PDC_path, vocabulary = dataset_min, length_normalize = True, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    

In [ ]:
UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)


In [ ]:
c = concatenate_embeddings([UKB,UKB], path='/home/concat.vec', vocabulary = dataset_min, method="generate",generate_method='cosine',k=10,where="return",normalize=True)
    

In [ ]:
results_to_csv(evaluate_on_all(c, lowercase_dataset=True))

In [ ]:
test_concat_avg()

In [ ]:
W2V.word_to_vector('Animalize')

In [ ]:
def normalize_vector(vector):
    vector = np.asarray(vector).reshape(-1,len(vector))
    return normalize(vector,norm='l2')[0]



In [ ]:
a1 = normalize_vector([100,100])
b1 = normalize_vector([100,100])
a2 = normalize_vector([1,0])
b2 = normalize_vector([0,1])

c1 = np.append(a1,a2)
c2 = np.append(b1,b2)

In [ ]:
a1 = [1,0.5]
b1 = [1*100,0.6*100]
a2 = [1,0.55]
b2 = [1,1]
a3 = [1.1, 0.55]
b3 = [0.9*100,0.6*100]

In [ ]:
calculate_cosine_simil(np.append(a1,a2), np.append(b1,b2))

In [ ]:
np.dot(np.append(a1,a2), np.append(b1,b2))

In [ ]:
np.linalg.norm(c1)*np.linalg.norm(c2)

In [ ]:
(pow(a1[0],2)+pow(a1[1],2))

In [ ]:
print(calculate_cosine_simil([100,100],[100,100]))
print(calculate_cosine_simil([1,0],[0,1]))

In [ ]:
calculate_cosine_simil(np.mean([a1,a2],axis=0), np.mean([b1,b2],axis=0))

In [ ]:
calculate_cosine_simil(np.append(a1,np.append(a2,a3)), np.append(b1,np.append(b2,b3)))

In [ ]:
cosine_2(np.append(a1,np.append(a2,a3)), np.append(b1,np.append(b2,b3)))

In [ ]:
calculate_cosine_simil(a3,b3)

In [ ]:
np.mean([a1,a2],axis=0)

In [ ]:
np.mean([b1,b2],axis=0)

In [ ]:
a1

In [ ]:
np.append(b1,b2)

In [ ]:
cosine_2([1,1,1],[1,9])

In [ ]:

def cosine_2(vector1, vector2):
    return np.dot(vector1/np.linalg.norm(vector1),vector2/np.linalg.norm(vector2))
    

In [ ]:
normalize_vector(np.append(b1,np.append(b2,b3)))

In [ ]:
np.append(b1,np.append(b2,b3))

In [ ]:
a1.reshape(3,)

In [ ]:
normalize_vector(UKB.vectors[1]).shape

In [ ]:
normalize_vector(UKB.vectors[1])[0]

In [ ]:
m = avg_embeddings([UKB,FT], path='/home/avg.vec', vocabulary = dataset_min, weights=None, method = "ignore",generate_method='cosine',k=10, where="return")
    

In [ ]:
results_to_csv(evaluate_on_all(m, lowercase_dataset=True))

In [ ]:
test_dim_reduction()

In [ ]:
#GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
#W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
#FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
SKE = load_embedding(SketchEngine_web_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)
PDC = load_embedding(PDC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)




In [ ]:
def test_l(emb):
    l = 0
    i = 0 
    
    for w in emb.vectors:
        l+= np.linalg.norm(w)
        i+=1
    
    return l/i


print('GLOVE: ' + str(test_l(GLOVE)))
print('W2V: ' + str(test_l(W2V)))
print('FT: ' + str(test_l(FT)))
print('jointcHYB: ' + str(test_l(jointcHYB)))
print('UKB: ' + str(test_l(UKB)))
print('LEXVEC: ' + str(test_l(LEXVEC)))

In [ ]:
print('SKE: ' + str(test_l(SKE)))
print('PDC: ' + str(test_l(PDC)))

In [ ]:
test_concatenate_auto([GLOVE,jointcHYB],['GLOVE','jointcHYB','"[50,1]"'],[50,1])
test_concatenate_auto([GLOVE,jointcHYB],['GLOVE','jointcHYB','"[25,1]"'],[25,1])
test_concatenate_auto([GLOVE,jointcHYB],['GLOVE','jointcHYB','"[100,1]"'],[100,1])

test_concatenate_auto([GLOVE,UKB],['GLOVE','UKB','"[50,1]"'],[50,1])
test_concatenate_auto([GLOVE,UKB],['GLOVE','UKB','"[25,1]"'],[25,1])
test_concatenate_auto([GLOVE,UKB],['GLOVE','UKB','"[100,1]"'],[100,1])
   

In [ ]:
test_concatenate_auto([GLOVE,jointcHYB],['GLOVE','jointcHYB','"[408.272727273,1]"'],[408.272727273,1])
test_concatenate_auto([W2V,UKB],['W2V','UKB','"[2.41470588235,1]"'],[2.41470588235,1])
test_concatenate_auto([LEXVEC,jointcHYB],['LEXVEC','jointcHYB','"[1.69343891403,1]"'],[1.69343891403,1])
test_concatenate_auto([LEXVEC,UKB],['LEXVEC','UKB','"[1.85746606335,1]"'],[1.85746606335,1])
test_concatenate_auto([LEXVEC,FT],['LEXVEC','FT','"[2.24660633484,1]"'],[2.24660633484,1])


In [ ]:
test_concatenate_auto([LEXVEC,FT],['LEXVEC','FT','"[2.24660633484,1]"'],[2.24660633484,1])

In [ ]:
test_retro('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/Results2/')

In [ ]:
directory = os.fsencode('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/Results2/prueba.txt')
print(str(os.path.basename(directory))[2:-1])

In [ ]:
print_variables()

In [ ]:
for name, obj in locals().items():
    if name != 'asizeof':
        print(asizeof.asizeof(obj) / 1024)

In [ ]:
test_reduction2('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/')

In [ ]:
 os.fsencode('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated')

In [ ]:
with open('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/W2V + jointcHYB.vec') as f:
        first_line = f.readline()
        first_line = first_line.split(' ')
        d = int(first_line[1])

In [ ]:
normalize_vector([1,2,3,4],'l2')

In [ ]:
test_concat_avg()

In [ ]:
np.linalg.norm([0.0757194,-0.0995169,-0.0203361,0.0117365,0.0259609,-0.0307204,-0.123747,-0.0287734,0.0995169,0.113363,0.036778,-0.0969208,-0.046297,-0.0302878,-0.013954,-0.0179563,-0.0305041,0.0443499,0.0244465,-0.0385087,-0.00603051,-0.0878345,-0.0273672,-0.0305041,0.0091945,-0.0899979,-0.0597101,-0.0722579,-0.0233648,0.0324512,0.112497,0.0188217,-0.028557,0.0222831,-0.0346146,0.0683638,0.074854,-0.0517055,0.0657677,-0.0454316,0.00762602,0.109469,0.0614409,-0.0254201,0.0105466,-0.0521382,0.0465133,-0.0527872,0.0395904,0.0488931,-0.00827505,-0.0467297,0.0224995,-0.00973535,0.028557,0.0471624,-0.0739887,0.0644697,0.0164419,0.0298551,-0.0861038,0.0631716,-0.0134131,0.028557,-0.0294224,0.00773419,0.0174155,-0.0696618,-0.0395904,0.0826423,-0.0886999,0.0393741,-0.128074,0.0203361,-0.0491094,-0.0398068,-0.0460807,-0.0791808,-0.038076,-0.0636043,-0.083075,-0.0982189,-0.112497,-0.0791808,-0.0588448,-0.0835077,-0.0947574,0.0960554,-0.0908633,-0.0674984,0.109469,-0.0696618,-0.0170909,-0.0108171,-0.010168,-0.00627389,0.0369943,0.036129,0.0255283,0.0670657,0.074854,0.0562487,0.0385087,-0.100382,0.11769,0.0121151,-0.0679311,0.0137917,0.0636043,0.123747,0.0235812,-0.0213096,0.0191462,0.0657677,-0.0307204,-0.000358315,-0.0666331,-0.0415375,0.0744213,0.0137917,-0.0588448,-0.0227158,-0.0315858,-0.0350473,0.148843,-0.00908633,0.00320455,0.0488931,-0.0253119,-0.0497585,0.0162256,0.0454316,0.0271508,0.0229322,-0.0400231,-0.0141703,-0.0584121,-0.0382924,0.0131427,-0.0465133,-0.0443499,-0.0232567,-0.0311531,-0.0709599,0.0107089,-0.0149275,0.0662004,-0.0666331,0.0208769,-0.0713926,0.156631,0.0575467,-0.0605755,0.0201197,0.0201197,0.00930267,-0.0236894,0.0458643,0.0791808,0.110334,-0.027908,0.0692292,0.00838322,0.13067,0.0122233,-0.0636043,-0.0168746,-0.0207687,0.11769,0.0908633,0.0426192,0.00581417,-0.0018389,-0.0679311,-0.0348309,-0.105574,0.00212285,-0.036778,0.0189298,-0.108603,-0.0016834,0.0597101,-0.0171991,-0.0917286,-0.0218505,-0.0666331,0.0631716,0.0106548,0.0943247,0.0140622,-0.0549506,0.022824,-0.0426192,-0.110767,0.00508402,-0.0157929,-0.0553833,-0.0391577,0.00757194,-0.0426192,0.0904306,-0.00109523,-0.00632798,0.0421865,0.0471624,-0.0506238,0.0783155,0.0255283,-0.019038,-0.0796135,-0.0904306,0.0493258,0.0623062,-0.0271508,0.0175236,0.0783155,-0.00800462,-0.0199034,-0.14192,0.0124937,-0.0501911,0.0402394,0.00224454,-0.0218505,-0.0212014,-0.0597101,-0.0136836,0.0333165,0.0904306,0.0181727,-0.0744213,-0.0307204,0.0326675,0.0311531,-0.0255283,-0.104709,-0.0426192,-0.0248792,0.101248,-0.140189,-0.006977,-0.0389414,-0.0605755,0.0627389,-0.137593,-0.0484604,-0.0106007,0.0200116,0.0395904,-0.0413212,0.0495421,0.00328568,-0.0113038,0.0744213,0.111632,-0.0700945,-0.064037,-0.0128182,-0.0181727,-0.0331002,0.0480277,-0.00822096,0.046297,-0.0601428,0.0426192,0.0215259,-0.0147112,-0.0791808,0.00762602,-0.029206,-0.0761521,0.0411048,-0.0389414,0.0107089,0.0454316,0.0432682,-0.00397527,0.0352636,0.127209,-0.0157929,-0.00951901,0.00402935,-0.0482441,-0.00160904,-0.101248,-0.0311531,0.0162256,0.0040564,0.00106818,-0.00092621,-0.0151439,-0.0243384,0.00578712,-0.0623062,0.0739887,0.0178481,0.0800462,-0.0391577,0.131535,-0.0250956])

In [ ]:
#FTo = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)   
FTretroWN = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/Results/FT_retro_WN+.txt', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)   
FTretroWNs = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/Results/FT_retro_WN.txt', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)   

ftretroPPDB = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/Results/FT_retro_ppdb.txt', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)   


In [ ]:
word1 = 'car'
word2 = 'mouse'

In [ ]:
calculate_cosine_simil(FTo.word_to_vector(word1),FTo.word_to_vector(word2))

In [ ]:
calculate_cosine_simil(FTretroWNs.word_to_vector(word1),FTretroWN.word_to_vector(word2))

In [ ]:
calculate_cosine_simil(FTretroWN.word_to_vector(word1),FTretroWN.word_to_vector(word2))

In [ ]:
calculate_cosine_simil(ftretroPPDB.word_to_vector(word1),ftretroPPDB.word_to_vector(word2))

In [ ]:
np.mean(cos_cdist(FTo.vectors,FTo.word_to_vector(word1)))

In [ ]:
np.mean(cos_cdist(FTretroWN.vectors,FTretroWN.word_to_vector(word1)))

In [ ]:
np.mean(cos_cdist(FTretroWNs.vectors,FTretroWNs.word_to_vector(word1)))

In [ ]:
np.mean(cos_cdist(ftretroPPDB.vectors,ftretroPPDB.word_to_vector(word1)))

In [ ]:
results_to_csv(evaluate_on_all(ftretroPPDB,lowercase_dataset=True),printRes=True,returnRes=False)
    

In [ ]:
results_to_csv(evaluate_on_all(FTretroWNs,lowercase_dataset=True),printRes=True,returnRes=False)
    

In [ ]:
FTretroWN2 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/FT_retro_WN+2.txt', vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)   
#FTretroWN15 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/FT_retro_WN+15.txt', vocabulary = dataset_min, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)   


In [ ]:
results_to_csv(evaluate_on_all(FTretroWN2,lowercase_dataset=True),printRes=True,returnRes=False)


In [ ]:
from subprocess import call
#print(str(datetime.datetime.now()) + ' ====> Test test_concat_avg')
#test_concat_avg()
#print(str(datetime.datetime.now()) + ' ====> Run script')
#with open("/home/iker/Escritorio/retro+.script", 'rb') as file:
#    script = file.read()
#rc = call(script, shell=True)
#del rc

#print(str(datetime.datetime.now()) + ' ====> Run test retro')
#test_retro('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/retrofitting-master/Results2/')

print(str(datetime.datetime.now()) + ' ====> Run add reduction')
add__reduction()

#print(str(datetime.datetime.now()) + ' ====> Run test reduction')
#test_reduction2('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/')


In [ ]:
#test_reduction2('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/Concatenated/')
test_reduction2('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/Done/extra/')


In [ ]:
print(str(datetime.datetime.now()) + ' ====> Run add reduction')
add__reduction()
print(str(datetime.datetime.now()) + ' ====> Run test reduction')
test_reduction2('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/ConcatenatedNoL2/')


In [ ]:
from subprocess import call

In [ ]:
def test_l(emb):
    l = 0
    i = 0 
    
    for w in emb.vectors:
        l+= np.linalg.norm(w)
        i+=1
    
    return l/i

In [ ]:
#GLOVE = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/GLOVE.FT-GLOVEL2.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#FT = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/FT.FT-UKB.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#UKB = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/UKB.FT-UKB.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#LEXVEC = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/LEXVEC.FT-LEXVEC.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
J = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/Jointc.FT-Jointc.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)

#N1 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/FTL1rm.Jointc-FTr.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#N2 = load_embedding('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/UKBrm.Jointc-UKBr.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)


In [ ]:
del G
del F
del U


G = deepcopy(GLOVE)
F = deepcopy(FT)
U = deepcopy(UKB)

In [ ]:
GLOVE.vectors = PPA(GLOVE.vectors)
FT.vectors = PPA(FT.vectors)
UKB.vectors = PPA(UKB.vectors)
J.vectors = PPA(J.vectors)

In [ ]:
gn = test_l(G)
fn = test_l(F)
un = test_l(U)


In [ ]:
c = avg_embeddings([UKB,FT,GLOVE,J], path='/home/concat.vec', vocabulary = dataset_min, weights=None, method="generate",generate_method='cosine',k=10,normalize=True, normalize_norm='l1', where="return")
results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=True,returnRes=False)
    

In [ ]:
del GLOVE
del FT
del UKB
del N1
del N2

In [ ]:
c = concatenate_embeddings([UKB,FT,J,GLOVE], path='/home/concat.vec', vocabulary = dataset_min, weights=None, method="generate",generate_method='cosine',k=10,normalize=True, where="return")
results_to_csv(evaluate_on_all(c,lowercase_dataset=True),printRes=True,returnRes=False)
    

In [ ]:
 with codecs.open('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/joint', "r",encoding='utf-8', errors='ignore') as fnodes:
        for line_no, line in enumerate(fnodes):
            print(line)

In [ ]:
directory = os.fsencode('/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/joint(Orto)')
files = os.listdir(directory)

for x in range(len(files)):
    for y in range(x,len(files)):
        print(str(files[x])+str(files[y]))
        
    

In [ ]:
l = list(itertools.permutations(files))

In [ ]:
files

In [ ]:
test_vecmap_FT_Orto()
test_vecmap_jointcHYB_Orto()


In [ ]:
test_vecmap_FT()
test_vecmap_jointcHYB()

In [ ]:
def print_n(normalize):
    print(normalize)

In [ ]:
print_n(False) calculate_cosine_simil

In [ ]:
#GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)
#FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
   
#W2V = load_embedding(W2V_path, vocabulary = None, format='bin', length_normalize = False, normalize_dimensionwise=False)
#jointcHYB = load_embedding(jointcHYB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
UKB = load_embedding(UKB_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#LEXVEC = load_embedding(lexvec, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#SKE = load_embedding(SketchEngine_web_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=100)
#PDC = load_embedding(PDC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
    

In [ ]:
generate_word(embedding,list_embs,word,overlapping_vocab=None,overlapping_matrix=None, annoy = None, number_of_words = 10, method = 'cosine'):

In [ ]:
c = avg_embeddings([FT,UKB], path='/home/concat.vec', vocabulary = dataset_min, weights=None, method="generate",generate_method='cosine',k=10,normalize=True, where="return")
results_to_csv(evaluate_on_all(c,lowercase_dataset=True))

In [ ]:
dogo = GLOVE.word_to_vector('dog')
caro = GLOVE.word_to_vector('car')
loveo = GLOVE.word_to_vector('love')

In [ ]:
i  = UKB.vocabulary.word_to_index('car')
UKB.vectors = np.delete(UKB.vectors,i,0)
del UKB.vocabulary.word_id['car']
del UKB.vocabulary.id_word[i]

In [ ]:
a = np.asarray([1,2,3,4])

In [ ]:
del GLOVE.vocabulary.words[i]

In [ ]:
GLOVE.word_to_vector('love')

In [ ]:
doge = generate_word(GLOVE,[GLOVE,FT],'dog',overlapping_vocab=None,overlapping_matrix=None, annoy = None, number_of_words = 11, method = 'cosine')
care = generate_word(GLOVE,[GLOVE,FT],'car',overlapping_vocab=None,overlapping_matrix=None, annoy = None, number_of_words = 11, method = 'cosine')
lovee = generate_word(GLOVE,[GLOVE,FT],'love',overlapping_vocab=None,overlapping_matrix=None, annoy = None, number_of_words = 11, method = 'cosine')

In [ ]:
doge = (GLOVE.word_to_vector('dogs')+GLOVE.word_to_vector('puppy')+GLOVE.word_to_vector('Dog')+GLOVE.word_to_vector('pet')+GLOVE.word_to_vector('cat')+GLOVE.word_to_vector('canine')+GLOVE.word_to_vector('puppies')+GLOVE.word_to_vector('terrier')+GLOVE.word_to_vector('pup')+GLOVE.word_to_vector('Dogs'))/10
care = (GLOVE.word_to_vector('cars')+GLOVE.word_to_vector('Car')+GLOVE.word_to_vector('vehicle')+GLOVE.word_to_vector('automobile')+GLOVE.word_to_vector('Cars')+GLOVE.word_to_vector('truck')+GLOVE.word_to_vector('vehicles')+GLOVE.word_to_vector('auto')+GLOVE.word_to_vector('driving')+GLOVE.word_to_vector('dealership'))/10
loveee = (GLOVE.word_to_vector('loved')+GLOVE.word_to_vector('loving')+GLOVE.word_to_vector('adore')+GLOVE.word_to_vector('LOVE')+GLOVE.word_to_vector('loves')+GLOVE.word_to_vector('Love')+GLOVE.word_to_vector('luv')+GLOVE.word_to_vector('hope')+GLOVE.word_to_vector('looove')+GLOVE.word_to_vector('loooove'))/10


In [ ]:

print(calculate_cosine_simil(doge,dogo))
print(calculate_cosine_simil(care,caro))
print(calculate_cosine_simil(lovee,loveo))


In [ ]:
UKB.word_to_vector('dog')

In [ ]:
overlapping_vocab[16161]

for w in range(len(overlapping_vocab)):
    if (overlapping_matrix[w]!=UKB.word_to_vector(overlapping_vocab[w])).all():
        print(w)
    print('h')

In [ ]:
UKB.word_to_vector('thickheaded')

In [ ]:
overlapping_matrix[16161]

In [ ]:
get_top_cosine_scipy(UKB.word_to_vector('dog'),UKB,k=10)

In [ ]:
ov = generate_overlapping_vocab([GLOVE,FT])
oe = generate_overlapping_matrix_embs(ov,[GLOVE,FT])

embs = ([GLOVE,FT])
ov2 = generate_overlapping_vocab(embs)
oe2 = generate_overlapping_matrix_embs(ov2,embs)

In [ ]:
i = 0
for w in a:
    if w == 'dog':
        break
    else:
        i+=1

In [ ]:
v = generate_overlapping_vocab([UKB])

In [ ]:
m = generate_overlapping_matrix_embs(v,[UKB])

In [ ]:
list(v)[400]

In [ ]:
list(v)

In [ ]:
list(set(v))

In [ ]:
UKB.word_to_vector('bitumen')

In [ ]:
 
    cos = cos_cdist(emb.vectors,vector)
    index =  get_largest_index(cos)
    top = []
    
    i = 0
    num = 0
    while i < len(index) & num<k:
        if emb.words[i] in overlap_vocab:
            top.append(emb.words[0])
            num+=1
        i+=1
    

In [ ]:
cos = cos_cdist(GLOVE.vectors,GLOVE.word_to_vector('dog'))
index =  get_largest_index(cos)

In [ ]:
overlap_vocab = set(GLOVE.words)

In [ ]:
i = 0
num = 0
top=[]
while i < len(index) and num<10:
    if GLOVE.words[index[i]] in overlap_vocab:
        top.append(GLOVE.words[index[i]])
        num+=1
    i+=1

In [ ]:
i < len(index) and num<10

In [ ]:
top = get_top_cosine_scipy(vector,emb_n,numer_of_word,overlapping_vocab,overlapping_matrix)

In [ ]:
matrix = []
    for w in overlapping_vocab:
        #matrix.append(emb.word_to_vector(w))
        matrix = np.append(matrix,emb.word_to_vector(w),axis=0)
    return matrix

In [ ]:
matrix=[]
matrix = np.append(matrix,[1,2,3,4],axis=1)

In [ ]:
set(set(['hola','que','ase']))

In [ ]:
matrix.append([1,2,3,4])

In [ ]:
matrix

In [22]:

path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/FT(Orto)/'

#GLOVEV = load_embedding(path+'GLOVE.FT-GLOVEL2.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
#FTV = load_embedding(path+'FT.FT-UKB.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
FT = load_embedding(FastText_CC_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
GLOVE = load_embedding(GLOVE_CC_840_path, vocabulary = None, length_normalize = False, normalize_dimensionwise=True, delete_duplicates=True, dims_restriction=300)


In [38]:
word = 'love'

In [39]:
cos = cos_cdist(FT.vectors,GLOVE.word_to_vector(word))
index =  get_largest_index(cos,10)

top = []
for i in index:
    top.append(FT.words[i])
top

['Clappison',
 '26yo',
 'Lazarowicz',
 'Koosh',
 'Westmacott',
 'Lightbown',
 'Stipetic',
 'Noff',
 'encouaged',
 'Saska']

In [40]:
cos = cos_cdist(FTV.vectors,GLOVEV.word_to_vector(word))
index =  get_largest_index(cos,10)

top = []
for i in index:
    top.append(FTV.words[i])
top

['love',
 'loving',
 'LOVE',
 'adore',
 'Love',
 'loved',
 'loves',
 'hate',
 'lovers',
 'lover']

In [41]:
calculate_cosine_simil(GLOVE.word_to_vector(word),FT.word_to_vector(word))

0.00443694

In [42]:
calculate_cosine_simil(GLOVEV.word_to_vector(word),FTV.word_to_vector(word))

0.6899997

In [15]:
test_concat_avg()

100%|██████████| 3000000/3000000 [00:45<00:00, 66369.10it/s]


 95%|█████████▍| 5543/5846 [06:12<00:20, 14.87it/s]WARNING:root:Word lustrate not found in any embedding.


100%|██████████| 5846/5846 [06:19<00:00, 15.39it/s]
INFO:root:The new embedding has 5814 word and vectors have 600 dimensions
100%|██████████| 2034/2034 [00:00<00:00, 51587.71it/s]


['preliterate' 'noncivilized']
['ruralist' 'rustic']
['ruralist' 'advocate']
['hypercoaster' 'roller']
['extravert' 'extroversive']
['deviationism' 'desertion']
['adventism' 'christianity']
['uncertainty' 'speculativeness']
['monsignori' 'priest']
['rotational' 'circumvolution']
['impossibilities' 'unattainableness']
['moderatorship' 'position']
['newness' 'brand-newness']
['sanctify' 'lustrate']
['heraldist' 'applaud']
['heraldist' 'tell']
['monotony' 'unvariedness']
['sublieutenant' 'lieutenant']
['incensing' 'odorize']
['embroiderers' 'embroideress']
['inconvertible' 'incommutable']
['diffidence' 'unassertiveness']
['incoordination' 'unskillfulness']
['monogenesis' 'reproduction']
['caesarism' 'autocracy']
['kazakhstani' 'asian']
['mildness' 'balminess']
['interpenetrate' 'spiritize']
['insecurities' 'insecureness']
['aerialist' 'ropewalker']
['nondescripts' 'person']
['internationalisms' 'scope']
['internationalisms' 'doctrine']
['latinist' 'classicist']
['constrict' 'astringe']


100%|██████████| 5846/5846 [02:40<00:00, 36.31it/s]
INFO:root:The new embedding has 5814 word and vectors have 600 dimensions
100%|██████████| 2034/2034 [00:00<00:00, 69679.54it/s]


...

100%|██████████| 5846/5846 [00:52<00:00, 111.28it/s]
INFO:root:The new embedding has 5844 words and vectors have 300 dimensions
100%|██████████| 2034/2034 [00:00<00:00, 79571.09it/s]


['monsignori' 'priest']
['internationalisms' 'scope']
['internationalisms' 'doctrine']


100%|██████████| 5846/5846 [00:48<00:00, 120.14it/s]
INFO:root:The new embedding has 5844 words and vectors have 300 dimensions
100%|██████████| 2034/2034 [00:00<00:00, 82616.37it/s]


['monsignori' 'priest']
['internationalisms' 'scope']
['internationalisms' 'doctrine']


100%|██████████| 5846/5846 [00:47<00:00, 122.19it/s]
INFO:root:The new embedding has 5846 word and vectors have 1900 dimensions
100%|██████████| 5846/5846 [00:48<00:00, 119.42it/s]
INFO:root:The new embedding has 5846 word and vectors have 1900 dimensions
100%|██████████| 5846/5846 [00:53<00:00, 109.83it/s]
INFO:root:The new embedding has 5846 word and vectors have 1900 dimensions
100%|██████████| 5846/5846 [00:51<00:00, 114.32it/s]
INFO:root:The new embedding has 5846 word and vectors have 1900 dimensions
100%|██████████| 5846/5846 [00:42<00:00, 137.58it/s]
INFO:root:The new embedding has 5846 word and vectors have 1900 dimensions
100%|██████████| 5846/5846 [00:41<00:00, 142.06it/s]
INFO:root:The new embedding has 5846 word and vectors have 1900 dimensions
100%|██████████| 5846/5846 [00:46<00:00, 126.61it/s]
INFO:root:The new embedding has 5846 word and vectors have 1900 dimensions
100%|██████████| 5846/5846 [00:45<00:00, 129.49it/s]
INFO:root:The new embedding has 5846 word and vecto

In [29]:
Top = load_embedding('/home/iker/Escritorio/Meta/avg.vec', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)


In [31]:
Top.L1_dimensionwwise()

In [32]:
results_to_csv(evaluate_on_all(Top,lowercase_dataset=True))

100%|██████████| 2034/2034 [00:00<00:00, 72429.78it/s]

['monsignori' 'priest']
['internationalisms' 'scope']
['internationalisms' 'doctrine']
0.6434964962286586,0.7728845388014604,0.8101669335623386,0.8593612431654819,0.8668068255841362,0.8619611306739761,0.8179271022075507,0.7688437098585119,0.8754778889455215,0.8044480045798984,0.7607321108693915,0.8846368238956354,0.5682822572288425,0.8741516009467072,0.8088846157604197,0.5764077323320247,0.6247643009627538,
1.0,1.0,1.0,1.0,1.0,1.0,1.0,1.0,1.0,1.0,1.0,1.0,1.0,1.0,1.0,1.0,0.9985250737463127,


In [22]:
evaluate_on_all(Top,lowercase_dataset=True)

100%|██████████| 2034/2034 [00:00<00:00, 75223.21it/s]

['monsignori' 'priest']
['internationalisms' 'scope']
['internationalisms' 'doctrine']


array([{'dataset': 'SimLex999', 'coverage': 1.0, 'pearson': 0.6662235410501283, 'spearman': 0.6404598488060838},
       {'dataset': 'MTurk-287', 'coverage': 1.0, 'pearson': 0.781966937140428, 'spearman': 0.7724961807592994},
       {'dataset': 'MTurk-771', 'coverage': 1.0, 'pearson': 0.7951002669089963, 'spearman': 0.80985608582461},
       {'dataset': 'MEN_DEV', 'coverage': 1.0, 'pearson': 0.8396025740468014, 'spearman': 0.8589625980494974},
       {'dataset': 'MEN_TEST', 'coverage': 1.0, 'pearson': 0.8531647520309281, 'spearman': 0.8654431268412633},
       {'dataset': 'MEN_ALL', 'coverage': 1.0, 'pearson': 0.8439572260816524, 'spearman': 0.8612290440145963},
       {'dataset': 'WS353_all', 'coverage': 1.0, 'pearson': 0.7797596549985749, 'spearman': 0.8167489511597438},
       {'dataset': 'WS353_relatedness', 'coverage': 1.0, 'pearson': 0.7545473118269888, 'spearman': 0.7671759499110585},
       {'dataset': 'WS353_similarity', 'coverage': 1.0, 'pearson': 0.8669118089252843, 'spearman

In [33]:
Top.export('/home/iker/Escritorio/Meta/FTr+UKBr-RotEmbeddings.vec')

100%|██████████| 2083053/2083053 [03:14<00:00, 10723.35it/s]


In [16]:
path = '/run/user/1000/gvfs/afp-volume:host=MyCloudEX2Ultra.local,user=iker,volume=My_Book_25EE-1/TFG/vecmap_results/vecmap-master/joint(Orto)/'
    
FT = load_embedding(path+'FT.Jointc-FT.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
UKB = load_embedding(path+'UKB.Jointc-UKB.Orto.TXT', vocabulary = None, length_normalize = False, normalize_dimensionwise=False, delete_duplicates=True, dims_restriction=300)
  

In [18]:
results_to_csv(evaluate_on_all(FT,lowercase_dataset=True))

100%|██████████| 2034/2034 [00:00<00:00, 61776.52it/s]

['preliterate' 'noncivilized']
['ruralist' 'rustic']
['ruralist' 'advocate']
['hypercoaster' 'roller']
['extravert' 'extroversive']
['deviationism' 'desertion']
['antedating' 'chronologize']
['adventism' 'christianity']
['uncertainty' 'speculativeness']
['monsignori' 'priest']
['rotational' 'circumvolution']
['impossibilities' 'unattainableness']
['winners' 'walloper']
['commandership' 'position']
['newness' 'brand-newness']
['heraldist' 'applaud']
['heraldist' 'tell']
['monotony' 'unvariedness']
['sublieutenant' 'lieutenant']
['americanize' 'change']
['incensing' 'odorize']
['embroiderers' 'embroideress']
['inconvertible' 'incommutable']
['diffidence' 'unassertiveness']
['monogenesis' 'reproduction']
['caesarism' 'autocracy']
['christianise' 'convert']
['kazakhstani' 'asian']
['nobelist' 'laureate']
['interpenetrate' 'spiritize']
['microphallus' 'penis']
['insecurities' 'insecureness']
['aerialist' 'ropewalker']
['postdates' 'chronologize']
['internationalisms' 'scope']
['internationa

In [19]:
results_to_csv(evaluate_on_all(UKB,lowercase_dataset=True))

  0%|          | 0/2034 [00:00<?, ?it/s]

['plays' 'losses']
['ship' 'ballots']
['saints' 'observatory']
['republicans' 'challenge']
['scottish' 'commuters']
['singapore' 'sanctions']
['rich' 'privileges']
['battle' 'prisoners']
['crime' 'assaulted']
['slaves' 'insured']
['cheers' 'musician']
['session' 'surprises']
['bulgarian' 'nurses']
['citizenship' 'casey']
['intelligence' 'troubles']
['salute' 'patterns']
['reichstag' 'germany']
['radiation' 'costumes']
['photography' 'proving']
['assassination' 'forbes']
['catholics' 'protestant']
['battle' 'warships']
['alcohol' 'fleeing']
['coil' 'ashes']
['explosive' 'builders']
['colonies' 'depression']
['diamond' 'killed']
['saints' 'repeal']
['operator' 'extracts']
['assassination' 'killed']
['birds' 'disturbances']
['palestinians' 'turks']
['chile' 'plates']
['exile' 'pledges']
['exile' 'threats']
['seizure' 'bishops']
['trade' 'farley']
['radical' 'bishops']
['crystal' 'oldest']
['patent' 'professionals']
['goverment' 'immunity']
['cardinals' 'villages']
['artillery' 'sanctions'

100%|██████████| 2034/2034 [00:00<00:00, 41879.83it/s]


['anticyclones' 'high']
['repositions' 'move']
['repositions' 'reduce']
['bounced' 'skip']
['bounced' 'bounce']
['kindergarteners' 'child']
['angrier' 'huffy']
['angrier' 'stormy']
['defiles' 'mar']
['defiles' 'spot']
['companionships' 'friendship']
['postboxes' 'maildrop']
['antedating' 'chronologize']
['benefited' 'help']
['benefited' 'get']
['interned' 'work']
['interned' 'confine']
['serenaded' 'perform']
['snookered' 'play']
['snookered' 'flim-flam']
['encroachments' 'inroad']
['encroachments' 'entrance']
['sentenced' 'declare']
['shrieks' 'shout']
['shrieks' 'cry']
['papered' 'cover']
['territorials' 'soldier']
['territorials' 'guard']
['transmigrating' 'immigrate']
['transmigrating' 'born']
['associations' 'southern']
['associations' 'sociable']
['planners' 'schemer']
['planners' 'notebook']
['combusts' 'blow']
['combusts' 'ablaze']
['producing' 'together']
['baggers' 'machine']
['baggers' 'workman']
['replications' 'reproduction']
['replications' 'procedure']
['retrials' 'tria